# Modelo de la demanada

## 1. Construcción de la base de datos para el modelo de absorción

En esta primera parte del código lo que hicimos fue **convertir los Excels operativos** (Ventas, Prototipos, Amenidades, etc.) en una tabla limpia y estructurada lista para modelar la **absorción mensual de vivienda por proyecto**.

La lógica general fue:

---

## 1.1. Definir la variable objetivo: Absorción Promedio Mensual

Creamos la función `calcular_absorcion_mensual(...)` para calcular, para cada proyecto y cada periodo de ventas, **cuántas viviendas se venden en promedio por mes**.

La idea de negocio detrás es:

- No es lo mismo vender 30 unidades en 1 mes que en 6 meses.
- La métrica relevante para comparar proyectos es la **velocidad de ventas**.

La función hace lo siguiente:

1. Unimos la hoja **Ventas** con las hojas **Vertical**, **Horizontal** y **Lote** para recuperar la `Fecha_inicio_venta` por proyecto.
2. Para cada proyecto:
   - En el **primer registro**:
     - Calculamos los meses entre la `Fecha_inicio_venta` y la primera `Fecha` en la hoja de ventas.
     - `Absorcion_prom_mensual = Ventas_periodo / meses_transcurridos`.
   - En los **registros siguientes**:
     - Calculamos los meses entre la fecha actual y la fecha del registro anterior.
     - Volvemos a dividir `Ventas_periodo / meses_del_periodo`.
3. Así obtenemos una columna nueva: **`Absorcion_prom_mensual`**, que será nuestra **variable objetivo (Y)**.

---

## 1.2. Incorporar el precio promedio por proyecto y fecha

Después trabajamos con la hoja **Precios**:

1. Aseguramos que la columna `Fecha` sea tipo fecha tanto en `precios_df` como en `ventas_con_abs_vf`.
2. Buscamos la columna de precio (en este caso `"Precio"`), la convertimos a numérica y **excluimos** los prototipos con precio `0`.
3. Calculamos el **precio promedio por proyecto y fecha**:

   - Agrupamos por `Fecha` y `Nombre_desarrollo`.
   - Tomamos el promedio de `Precio` y lo renombramos como `Precio_promedio`.

4. Hacemos un `merge` para agregar `Precio_promedio` a la tabla de ventas con absorción (`ventas_con_abs_vf`).

---

## 1.3. Incorporar el M2 promedio y el Precio por m²

Repetimos la misma lógica, pero ahora para los metros cuadrados:

1. Identificamos la columna de m² (en este caso `"M2"`).
2. Convertimos la columna a numérica y filtramos registros con m² > 0.
3. Calculamos el **M2 promedio por proyecto y fecha**: `M2_promedio`.
4. Volvemos a hacer un `merge` con la tabla principal.

Con esto podemos construir:

- `Precio_por_M2 = Precio_promedio / M2_promedio`

que es una forma más comparable de ver el precio entre proyectos de distinto tamaño.

---

## 1.4. Rellenar precio en periodos sin inventario

Hay fechas donde:

- El inventario disponible es 0.
- No hay registro de precio ese mes.
- Pero el proyecto no está marcado como "Ventas detenidas".

Para no perder esos registros:

1. Ordenamos la tabla por `Nombre_desarrollo`, `Tipo_proyecto` y `Fecha`.
2. Calculamos un **forward fill** del precio por proyecto y tipo:
   - `Precio_promedio_ffill = precio_promedio` arrastrado desde el último precio conocido.
3. Donde:
   - `Inventario_disponible == 0`
   - `Precio_promedio` es nulo
   - `Ventas_detenidas != 1`
   
   rellenamos `Precio_promedio` con `Precio_promedio_ffill`.

Así mantenemos continuidad de información de precio sin inventarnos datos nuevos: solo reutilizamos el último precio conocido del mismo proyecto.

---

## 1.5. Transformar Amenidades a variables utilizables en modelo

Las amenidades vienen originalmente como una lista de IDs (`"2,3,12"`). Eso no es usable directamente por un modelo, así que:

1. Creamos la función `procesar_amenidades(...)`:
   - Lee la hoja **Amenidades** (Id y nombre de cada amenidad).
   - Crea una columna binaria por amenidad:  
     - Ejemplo: `amen_Alberca`, `amen_Gimnasio`, `amen_Pool_Bar`, etc.
   - Si un prototipo tiene la amenidad, esa columna vale `1`, si no `0`.

2. Aplicamos esta función a:
   - `vertical_df` → `vertical_amen`
   - `horizontal_df` → `horizontal_amen`
   - `lote_df` → `lote_amen`

3. Eliminamos columnas que **no tienen sentido promediar** o no son útiles para el modelo (dirección, texto descriptivo, fechas de obra, etc.).




In [ ]:
# ============================================================
# 0. CONFIGURACIÓN INICIAL
# ============================================================

# Librerías básicas
import pandas as pd
pd.set_option('display.float_format', lambda x: '%.2f' % x)

import numpy as np
import matplotlib.pyplot as plt

# Machine Learning
from sklearn.model_selection import train_test_split
from sklearn.compose import ColumnTransformer
from sklearn.preprocessing import OneHotEncoder 
from sklearn.impute import SimpleImputer
from sklearn.pipeline import Pipeline
from xgboost import XGBRegressor
from sklearn.model_selection import TimeSeriesSplit


from sklearn.metrics import r2_score, mean_squared_error
import numpy as np


# Guardar / cargar modelos
import joblib
from pathlib import Path

# Para warnings
import warnings
warnings.filterwarnings("ignore")

# ============================================================
#  Funciones auxiliares
# ============================================================

#  CÁLCULO DE ABSORCIÓN PROMEDIO MENSUAL POR PROYECTO
def calcular_absorcion_mensual(
    ventas_df,
    vertical_df,
    horizontal_df,
    lote_df,
    col_fecha_ventas="Fecha",
    col_fecha_inicio="Fecha_inicio_venta",
    col_tipo="Tipo_proyecto",
    col_desarrollo="Nombre_desarrollo",
    col_ventas_periodo="Ventas_periodo"
):
    """
    Calcula la absorción promedio mensual por proyecto, usando:
      - ventas_df: hoja Ventas
      - vertical_df, horizontal_df, lote_df: hojas de producto para obtener Fecha_inicio_venta
    
    Lógica:
      - Para cada proyecto (Nombre_desarrollo) y tipo (Tipo_proyecto):
          * Primer registro:
                meses = meses entre Fecha_inicio_venta y primera Fecha en ventas_df
                absorción = Ventas_periodo / meses
          * Registros siguientes:
                meses = meses entre Fecha actual y Fecha anterior de ese desarrollo
                absorción = Ventas_periodo / meses
    
    Devuelve:
      - DataFrame de ventas con una nueva columna: 'Absorcion_prom_mensual'
    """
    ventas = ventas_df.copy()
    
    # Asegurar tipos datetime
    ventas[col_fecha_ventas] = pd.to_datetime(ventas[col_fecha_ventas])
    
    for df in [vertical_df, horizontal_df, lote_df]:
        if col_fecha_inicio in df.columns:
            df[col_fecha_inicio] = pd.to_datetime(df[col_fecha_inicio])
    
    # Función auxiliar para obtener tabla (Nombre_desarrollo -> Fecha_inicio_venta) por tipo
    def build_inicio_df(df_prod, tipo_label):
        if col_fecha_inicio not in df_prod.columns:
            return pd.DataFrame(columns=[col_desarrollo, col_fecha_inicio, col_tipo])
        
        tmp = df_prod[[col_desarrollo, col_fecha_inicio]].dropna().copy()
        # Si hay varias filas por desarrollo, nos quedamos con la fecha mínima (primer inicio)
        tmp = (
            tmp
            .sort_values(col_fecha_inicio)
            .drop_duplicates(subset=[col_desarrollo], keep="first")
        )
        tmp[col_tipo] = tipo_label
        return tmp
    
    inicio_vertical   = build_inicio_df(vertical_df,   "Vertical")
    inicio_horizontal = build_inicio_df(horizontal_df, "Horizontal")
    inicio_lote       = build_inicio_df(lote_df,       "Lote")
    
    inicio_todos = pd.concat(
        [inicio_vertical, inicio_horizontal, inicio_lote],
        ignore_index=True
    )
    
    # Unimos ventas con Fecha_inicio_venta según Tipo_proyecto + Nombre_desarrollo
    ventas = ventas.merge(
        inicio_todos,
        on=[col_desarrollo, col_tipo],
        how="left",
        suffixes=("", "_inicio")
    )
    
    # Ordenamos por proyecto, tipo y fecha
    ventas = ventas.sort_values([col_tipo, col_desarrollo, col_fecha_ventas]).reset_index(drop=True)
    
    # Fecha previa por proyecto y tipo (dentro de ventas_df)
    ventas["Fecha_prev"] = (
        ventas
        .groupby([col_tipo, col_desarrollo])[col_fecha_ventas]
        .shift(1)
    )
    
    # Para la primera fila de cada desarrollo, usamos Fecha_inicio_venta
    mask_first = ventas["Fecha_prev"].isna()
    ventas.loc[mask_first, "Fecha_prev"] = ventas.loc[mask_first, col_fecha_inicio]
    
    # Cálculo de meses de diferencia: (año*12 + mes)
    meses_diff = (
        ventas[col_fecha_ventas].dt.year * 12 + ventas[col_fecha_ventas].dt.month
        - (ventas["Fecha_prev"].dt.year * 12 + ventas["Fecha_prev"].dt.month)
    )
    
    # Evitar 0 o negativos (si algo raro pasa, ponemos 1 mes mínimo)
    meses_diff = meses_diff.clip(lower=1)
    
    ventas["Meses_periodo_calculados"] = meses_diff
    
    # Absorción promedio mensual
    ventas["Absorcion_prom_mensual"] = ventas[col_ventas_periodo] / ventas["Meses_periodo_calculados"]
    
    return ventas


# ---------------------------------------------
#   Función: procesar columna de Amenidades
# ---------------------------------------------

def procesar_amenidades(df_prod, amenidades_df, col_amenidades="Amenidades", prefix="amen_"):
    """
    Convierte la columna de IDs de amenidades (e.g. '2,3,12')
    en variables binarias amen_X para cada amenidad definida
    en la hoja Amenidades.
    
    Parámetros:
    -----------
    df_prod : DataFrame
        Hoja Vertical / Horizontal / Lote.
    amenidades_df : DataFrame
        Debe contener columnas de ID y nombre de la amenidad.
    col_amenidades : str
        Nombre de la columna con IDs separados por coma.
    prefix : str
        Prefijo para las columnas dummy.
    """
    df = df_prod.copy()
    
    # Detectar columnas de ID y nombre en amenidades_df
    posibles_id_cols = ["Id_amenidades"]
    posibles_name_cols = ["Amenidad"]
    
    col_id = next((c for c in posibles_id_cols if c in amenidades_df.columns), None)
    col_name = next((c for c in posibles_name_cols if c in amenidades_df.columns), None)
    
    if col_id is None or col_name is None:
        raise ValueError(
            f"No se encontraron columnas de ID/nombre en amenidades_df. "
            f"Columnas disponibles: {amenidades_df.columns.tolist()}"
        )
    
    id_to_name = dict(zip(amenidades_df[col_id], amenidades_df[col_name]))
    
    # Crear columnas binarias (inicialmente en 0)
    for name in amenidades_df[col_name]:
        safe_name = str(name).strip().replace(" ", "_")
        col_bin = f"{prefix}{safe_name}"
        df[col_bin] = 0
    
    # Marcar 1 donde aplique
    for idx, row in df.iterrows():
        raw = row.get(col_amenidades)
        if pd.isna(raw):
            continue
        ids = str(raw).split(",")
        for id_str in ids:
            id_str = id_str.strip()
            if id_str == "":
                continue
            try:
                id_int = int(id_str)
            except ValueError:
                continue
            amen_name = id_to_name.get(id_int)
            if amen_name is not None:
                safe_name = str(amen_name).strip().replace(" ", "_")
                col_bin = f"{prefix}{safe_name}"
                df.at[idx, col_bin] = 1
    
    return df


# ------------------------------------------------------------
# RUTA DEL ARCHIVO EXCEL
# ------------------------------------------------------------
excel_path = Path(r"C:\Users\julio\OneDrive\Documentos\Trabajo\Ideas Frescas\Proyectos\REM\BD\BD_Mazatlan.xlsm")  # <- AJUSTA A TU RUTA LOCAL

assert excel_path.exists(), f"El archivo {excel_path} no se encontró. Revisa la ruta."


# ============================================================
# 1. CARGA DE DATOS DESDE EXCEL
# ============================================================

# Cargar el libro de Excel
xls = pd.ExcelFile(excel_path)

# Cargar únicamente las hojas que nos interesan
ventas_df         = pd.read_excel(excel_path, sheet_name="Ventas")
precios_df        = pd.read_excel(excel_path, sheet_name="Precios")
vertical_df       = pd.read_excel(excel_path, sheet_name="Vertical")
horizontal_df     = pd.read_excel(excel_path, sheet_name="Horizontal")
lote_df           = pd.read_excel(excel_path, sheet_name="Lote")
amenidades_df     = pd.read_excel(excel_path, sheet_name="Amenidades")  
creditos_df       = pd.read_excel(excel_path, sheet_name="Creditos")

# Hojas de información de prototipos:
info_vert_df      = pd.read_excel(excel_path, sheet_name="Info_Prototipos_vertical")
info_horiz_df     = pd.read_excel(excel_path, sheet_name="Info_Prototipos_horizontal")
info_lote_df      = pd.read_excel(excel_path, sheet_name="Info_Prototipos_lote")

# ============================================================
# Limpieza de datos
# ============================================================

# Se eliminan filas con 'Tipo_proyecto' nulo o '-'
ventas_df = ventas_df[ventas_df['Tipo_proyecto'].notna() & (ventas_df['Tipo_proyecto'] != '-')]


# ------------------------------------------------------------
# APLICAR LA FUNCIÓN
# ------------------------------------------------------------

ventas_con_abs = calcular_absorcion_mensual(
    ventas_df=ventas_df,
    vertical_df=vertical_df,
    horizontal_df=horizontal_df,
    lote_df=lote_df
)

ventas_con_abs_vf = ventas_con_abs[
    ["Fecha", "Nombre_desarrollo", "Tipo_proyecto", "Ventas_acumuladas",
     "Ventas_periodo", "Inventario_disponible", "Numero_de_viviendas_planeadas",
     "Absorcion_prom_mensual", "Ventas_detenidas"]

]

# ============================================================
#   AGREGAR PRECIO PROMEDIO POR FECHA Y DESARROLLO
#    (ignorando prototipos con precio = 0)
# ============================================================

# Aseguramos que la fecha sea datetime en ambos DF
precios_df["Fecha"] = pd.to_datetime(precios_df["Fecha"])
ventas_con_abs_vf["Fecha"] = pd.to_datetime(ventas_con_abs_vf["Fecha"])

# --- 1) Columna de precio ---
posibles_cols_precio = ["Precio"]
col_precio = None
for c in posibles_cols_precio:
    if c in precios_df.columns:
        col_precio = c
        break

if col_precio is None:
    raise ValueError(
        f"No se encontró ninguna columna de precio en precios_df. "
        f"Revisa el nombre (ej. 'Precio', 'Precio_final'). "
        f"Columnas disponibles: {precios_df.columns.tolist()}"
    )

# Convertimos a numérico por si viene como texto con símbolos
precios_df[col_precio] = pd.to_numeric(precios_df[col_precio], errors="coerce")

# --- 2) Filtrar precios > 0 para NO contarlos en el promedio ---
precios_validos = precios_df[precios_df[col_precio] > 0].copy()

# --- 3) Calcular precio promedio por Fecha + Nombre_desarrollo ---
precios_promedio = (
    precios_validos
    .groupby(["Fecha", "Nombre_desarrollo"], as_index=False)[col_precio]
    .mean()
    .rename(columns={col_precio: "Precio_promedio"})
)

# --- Hacer el merge con ventas_con_abs_vf ---
ventas_con_precio = ventas_con_abs_vf.merge(
    precios_promedio,
    on=["Fecha", "Nombre_desarrollo"],
    how="left"
)


# ============================================================
# 3.1 AGREGAR M2 PROMEDIO POR FECHA Y DESARROLLO
#    (ignorando prototipos con M2 = 0)
# ============================================================

# --- 1) Elegir la columna de m2 ---
posibles_cols_m2 = ["M2"]
col_m2 = None
for c in posibles_cols_m2:
    if c in precios_df.columns:
        col_m2 = c
        break

if col_m2 is None:
    raise ValueError(
        f"No se encontró ninguna columna de m2 en precios_df. "
        f"Revisa el nombre (ej. 'M2', 'M2_construccion'). "
        f"Columnas disponibles: {precios_df.columns.tolist()}"
    )

# Aseguramos tipo numérico
precios_df[col_m2] = pd.to_numeric(precios_df[col_m2], errors="coerce")

# --- 2) Filtrar m2 > 0 ---
m2_validos = precios_df[precios_df[col_m2] > 0].copy()

# --- 3) Calcular m2 promedio por Fecha + Nombre_desarrollo ---
m2_promedio = (
    m2_validos
    .groupby(["Fecha", "Nombre_desarrollo"], as_index=False)[col_m2]
    .mean()
    .rename(columns={col_m2: "M2_promedio"})
)

# --- 4) Hacer el merge con ventas_con_precio ---
ventas_con_precio = ventas_con_precio.merge(
    m2_promedio,
    on=["Fecha", "Nombre_desarrollo"],
    how="left"
)


# ============================================================
# 3.2 RELLENAR Precio_promedio CUANDO INVENTARIO = 0
#     USANDO EL PRECIO PROMEDIO ANTERIOR (SI NO HAY VENTAS DETENIDAS)
# ============================================================

# Aseguramos que esté ordenado por desarrollo, tipo y fecha
ventas_con_precio_M2 = ventas_con_precio.sort_values(
    ["Nombre_desarrollo", "Tipo_proyecto", "Fecha"]
).reset_index(drop=True)

# Crear una columna auxiliar con el forward-fill del precio por desarrollo+tipo
ventas_con_precio_M2["Precio_promedio_ffill"] = (
    ventas_con_precio_M2
    .groupby(["Nombre_desarrollo", "Tipo_proyecto"])["Precio_promedio"]
    .ffill()
)

# Máscara de filas donde queremos rellenar:
# - Inventario_disponible == 0
# - Precio_promedio es NaN
# - Ventas_detenidas != 1
mask_rellenar = (
    (ventas_con_precio_M2["Inventario_disponible"] == 0) &
    (ventas_con_precio_M2["Precio_promedio"].isna()) &
    (ventas_con_precio_M2["Ventas_detenidas"] != 1)
)

# Aplicar el relleno solo en las filas que cumplen la condición
ventas_con_precio_M2.loc[mask_rellenar, "Precio_promedio"] = \
    ventas_con_precio_M2.loc[mask_rellenar, "Precio_promedio_ffill"]

# Eliminar columna auxiliar
ventas_con_precio_M2 = ventas_con_precio_M2.drop(columns=["Precio_promedio_ffill"])

# Verificar ejemplo para un desarrollo
ventas_con_precio_M2[
    ventas_con_precio_M2["Nombre_desarrollo"] == "Almarena- Casas"
][
    ["Fecha", "Nombre_desarrollo", "Inventario_disponible",
     "Ventas_detenidas", "Precio_promedio"]
]


#Calcular precio por M2
ventas_con_precio_M2["Precio_por_M2"] = ventas_con_precio_M2["Precio_promedio"] / ventas_con_precio_M2["M2_promedio"]

# Parsear amenidades y quitar columnas no deseadas

# Aplicar la función procesar_amenidades
vertical_amen   = procesar_amenidades(vertical_df,   amenidades_df, col_amenidades="Amenidades", prefix="amen_")
horizontal_amen = procesar_amenidades(horizontal_df, amenidades_df, col_amenidades="Amenidades", prefix="amen_")
lote_amen       = procesar_amenidades(lote_df,       amenidades_df, col_amenidades="Amenidades", prefix="amen_")


# Quitamos columnas que NO queremos agregar promediando 
col_drop = ["Direccion", "Latitud", "Longitud","Desarrolladora","Comercializadora", "Segementación ", "Número_de_etapas_total_planeadas","Etapa_actual","Material_constucción",
            "Número_niveles","Descripción_departamento_x_torre","Tipo_fraccionamiento","Acceso_desarrollo","Vigilancia","Regimen_condominio","Couota_mantenimineto","Otro",
            "Instalacion_Gas_lp","Instalaciones_electricas","Cisterna","Credito_puente","Precio_de_preventa","Creditos_aceptados",	"%_enganche",
            "Fecha_primer_levantamiento","Fecha_estimada_entrega",	"Fecha_entrega_ofical",	"Fecha_inicio_construcción","Fecha_estimada_fin_contruccion",
            "Fecha_fin_construcción","Amenidades", 'Fecha_fin_ventas','Meses_venta',"Número_unida_1_recamara",	"Número_unida_2_recamara",	"Número_unida_3_recamara","Estatus_obra","Estatus_venta","Departamentos_planeados"]

# Quitamos columnas que NO queremos agregar promediando 
col_drop_2 = ["Direccion", "Latitud", "Longitud","Desarrolladora","Comercializadora", "Segementación ", "Número_de_etapas_total_planeadas","Etapa_actual","Material_constucción",
            "Tipo_fraccionamiento","Acceso_desarrollo","Vigilancia","Couota_mantenimineto","Otro",
            "Instalacion_Gas_lp","Instalaciones_electricas","Cisterna","Credito_puente","Creditos_aceptados","%_enganche",
            "Fecha_primer_levantamiento","Fecha_estimada_entrega",	"Fecha_entrega_ofical",	"Fecha_inicio_construcción","Fecha_estimada_fin_contruccion","Fecha_fin_construcción","Amenidades", 'Fecha_fin_ventas','Meses_venta',"Número_unida_1_recamara",	"Número_unida_2_recamara",	"Número_unida_3_recamara","Estatus_obra",	"Estatus_venta"	]

# Quitamos columnas que NO queremos agregar promediando 
col_drop_3 = ["Direccion", "Latitud", "Longitud","Desarrolladora","Comercializadora", "Segementación ","Etapa_actual",
            "Tipo_fraccionamiento","Acceso_desarrollo","Vigilancia","Couota_mantenimineto","Otro",
            "Credito_puente","Creditos_aceptados",	"%_enganche",
            "Fecha_primer_levantamiento","Fecha_estimada_entrega",	"Fecha_entrega_ofical",	"Fecha_inicio_construcción","Fecha_estimada_fin_contruccion","Fecha_fin_construcción","Amenidades", 'Fecha_fin_ventas','Meses_venta',"Estatus_obra",	"Estatus_venta"	]

# Eliminar columnas no deseadas
vertical_amen.drop(columns=col_drop, inplace=True)
# Eliminar columnas de amenidades que no están presentes en ningún proyecto
vertical_amen = vertical_amen.drop(
    columns=vertical_amen.iloc[:, 10:].columns[
        vertical_amen.iloc[:, 10:].sum() == 0
    ]
)


horizontal_amen.drop(columns=col_drop_2, inplace=True)
# Eliminar columnas de amenidades que no están presentes en ningún proyecto
horizontal_amen = horizontal_amen.drop(
    columns=horizontal_amen.iloc[:, 13:].columns[
        horizontal_amen.iloc[:, 13:].sum() == 0
    ]
)


lote_amen.drop(columns=col_drop_3, inplace=True)
# Eliminar columnas de amenidades que no están presentes en ningún proyecto
lote_amen = lote_amen.drop(
    columns=lote_amen.iloc[:, 14:].columns[
        lote_amen.iloc[:, 14:].sum() == 0
    ]
)


ventas_con_precio_M2.head(10)


In [ ]:
vertical_df['Nombre_desarrollo'=]

In [ ]:
precios_df[precios_df['Nombre_desarrollo']=='Alba Condominios']

In [ ]:
ventas_df[ventas_df['Nombre_desarrollo']=='Cordelia Seminario-Departamentos']

In [ ]:
ventas_con_precio_M2.describe()

# Vertical

---

## 1.6. Filtro hacia el universo de análisis: proyectos verticales activos

Antes de modelar, definimos claramente **qué universo queremos estudiar**:

1. Nos enfocamos sólo en **proyectos Verticales**

2. Excluimos un caso particular que contamina el análisis:

- Aguamarina Talismán

3. Excluimos proyectos con ventas detenidas:

4. Finalmente, construimos el dataset final para modelar:




En resumen, al terminar esta etapa tenemos:

- Una tabla donde cada fila es:

    - Un proyecto vertical en una fecha específica.

- Con columnas que representan:

    - Velocidad de ventas (absorción mensual).

     - Precio, m², precio por m².

    - Inventario y viviendas planeadas.

    - Amenidades (en formato binario).

    - Señales limpias y consistentes para poder entrenar un modelo de Machine Learning más adelante.


In [ ]:
# Preparar datos agregados por tipo de proyecto
# ============================================================

# AFiltro por tipo de proyecto: vertical
ventas_vertical = ventas_con_precio_M2[ventas_con_precio_M2["Tipo_proyecto"] == "Vertical"]

#Se esxcluye Aguamarina Talismán
ventas_vertical = ventas_vertical[(ventas_vertical['Nombre_desarrollo']!='Aguamarina Talismán')& (ventas_vertical['Nombre_desarrollo']!='Camila Hills Departametos')]

# Filtrar por proyectos detenidos 
ventas_vertical = ventas_vertical[ventas_vertical['Ventas_detenidas']==0]


# ============================================================
# DATASET FINAL DE MODELADO (Y vs X_int)
# ============================================================

ventas_vertical_df = ventas_vertical.merge(
    vertical_amen,
    on=["Nombre_desarrollo"],
    how="left",
    
)

ventas_vertical_df.head()

In [ ]:
# ============================================================
# DATASET DE MODELADO PARA VERTICAL: Y vs X_int
# ============================================================
df_v = ventas_vertical_df.copy()
df_v["Fecha"] = pd.to_datetime(df_v["Fecha"])
df_v = df_v[df_v["Absorcion_prom_mensual"].notna()].reset_index(drop=True)
df_v = df_v.sort_values("Fecha").reset_index(drop=True)

# ============================================================
# 1) VARIABLES TEMPORALES
# ============================================================
df_v["Mes"] = df_v["Fecha"].dt.month
df_v["Año"] = df_v["Fecha"].dt.year
df_v["Trimestre"] = df_v["Fecha"].dt.quarter
df_v["Mes_sincronico"] = ((df_v["Año"] - df_v["Año"].min()) * 12) + df_v["Mes"]

# ESTACIONALIDAD CÍCLICA
df_v["Mes_sin"] = np.sin(2 * np.pi * df_v["Mes"] / 12)
df_v["Mes_cos"] = np.cos(2 * np.pi * df_v["Mes"] / 12)

# ============================================================
# 2) MOMENTUM DEL PROYECTO (CICLO DE VIDA)
# ============================================================
df_v["Avance_ventas"] = df_v["Ventas_acumuladas"] / df_v["Numero_de_viviendas_planeadas"]
df_v["Avance_lag1"] = df_v.groupby("Nombre_desarrollo")["Avance_ventas"].shift(1)

# ============================================================
# 3) LAGS Y PROMEDIOS MÓVILES POR PROYECTO
# ============================================================
grp = df_v.groupby("Nombre_desarrollo")["Absorcion_prom_mensual"]

df_v["Abs_lag_1"] = grp.shift(1)

df_v["Abs_roll_3"] = grp.transform(
    lambda s: s.rolling(3, min_periods=2).mean().shift(1)
)

df_v["Abs_roll_6"] = grp.transform(
    lambda s: s.rolling(6, min_periods=3).mean().shift(1)
)

# Inventario y precio históricos
df_v["Pct_inventario"] = df_v["Inventario_disponible"] / df_v["Numero_de_viviendas_planeadas"]
df_v["Pct_inv_lag1"] = df_v.groupby("Nombre_desarrollo")["Pct_inventario"].shift(1)

# Precio promedio lag 1
df_v["Precio_lag1"] = df_v.groupby("Nombre_desarrollo")["Precio_promedio"].shift(1)

# LIMPIAR FILAS DONDE NO EXISTEN LAGS MÍNIMOS
df_v = df_v.dropna(subset=["Abs_lag_1","Abs_roll_3","Abs_roll_6","Pct_inv_lag1","Precio_lag1","Avance_lag1"])



# Precio relativo del proyecto contra su competencia en ese mes
# Esto es CRÍTICO en inmobiliario.
# La absorción no depende del precio absoluto, sino del precio relativo.
# Precio promedio del mercado por mes
precio_mercado = df_v.groupby("Fecha")["Precio_promedio"].mean().rename("Precio_mercado")

df_v = df_v.merge(precio_mercado, on="Fecha", how="left")
df_v["Precio_relativo"] = df_v["Precio_promedio"] / df_v["Precio_mercado"]

# lag
df_v["Precio_rel_lag1"] = df_v.groupby("Nombre_desarrollo")["Precio_relativo"].shift(1)



# Inventario relativo (no absoluto)
# No es igual tener 50 unidades disponibles en un mercado con 200 unidades, que en un mercado con 900.
inv_total = df_v.groupby("Fecha")["Inventario_disponible"].sum().rename("Inventario_total")

df_v = df_v.merge(inv_total, on="Fecha", how="left")
df_v["Inventario_relativo"] = df_v["Inventario_disponible"] / df_v["Inventario_total"]
df_v["Inventario_rel_lag1"] = df_v.groupby("Nombre_desarrollo")["Inventario_relativo"].shift(1)



# Competencia activa ese mes
# Cuántos proyectos compiten contigo ese mes.
df_v["Competidores_mes"] = df_v.groupby("Fecha")["Nombre_desarrollo"].transform("nunique")



# Agregar cambios (deltas) en lugar de valores absolutos
# Los cambios predicen mejor que los niveles.
df_v["Delta_precio"] = df_v["Precio_promedio"] - df_v["Precio_lag1"]
df_v["Delta_abs_3m"] = df_v["Abs_roll_3"] - df_v["Abs_lag_1"]
df_v["Delta_avance"] = df_v["Avance_ventas"] - df_v["Avance_lag1"]

# ============================================================
# 4) LIMPIAR AMENIDADES DE VARIANZA BAJA
# ============================================================
amen_cols = [c for c in df_v.columns if c.startswith("amen_")]
for col in amen_cols:
    if df_v[col].sum() < 5:
        df_v = df_v.drop(columns=[col])

# ============================================================
# 5) DEFINIR TARGET Y FEATURES
# ============================================================
y = df_v["Absorcion_prom_mensual"].values

cols_excluir = [
    "Absorcion_prom_mensual",
    "Fecha",
    "Nombre_desarrollo",
    "Tipo_proyecto",

    # Leakage
    "Ventas_acumuladas",
    "Ventas_periodo",
    "Inventario_disponible",
    "Numero_de_viviendas_planeadas",

    # Variables del mismo periodo
    "Precio_promedio",
    "Pct_inventario",
    "Precio_por_M2",
    "Avance_ventas",
]

X = df_v.drop(columns=cols_excluir)

# ============================================================
# 6) PREPROCESAMIENTO
# ============================================================
numeric_features = X.select_dtypes(include=[np.number]).columns.tolist()
categorical_features = X.select_dtypes(include=["object","category"]).columns.tolist()

for col in categorical_features:
    X[col] = X[col].astype("string").fillna("Missing")

categorical_transformer = Pipeline([
    ("imputer", SimpleImputer(strategy="most_frequent")),
    ("onehot", OneHotEncoder(handle_unknown="ignore")),
])

preprocess = ColumnTransformer([
    ("cat", categorical_transformer, categorical_features),
    ("num", "passthrough", numeric_features),
])

# ============================================================
# 7) MODELO REGULARIZADO
# ============================================================
xgb_model = XGBRegressor(
    n_estimators=500,
    learning_rate=0.03,
    max_depth=3,
    min_child_weight=5,
    subsample=0.7,
    colsample_bytree=0.7,
    reg_lambda=2,
    reg_alpha=2,
    objective="reg:squarederror",
    random_state=42,
    n_jobs=-1,
)

modelo_v2 = Pipeline([
    ("preprocess", preprocess),
    ("model", xgb_model),
])


def rmse(a, b):
    return np.sqrt(mean_squared_error(a, b))

# ============================================================
# 8) TIME SERIES CROSS-VALIDATION
# ============================================================
tscv = TimeSeriesSplit(n_splits=4)

fold_results = []
print("=== Time Series Cross-Validation (4 folds) ===")

for fold, (train_idx, test_idx) in enumerate(tscv.split(X), start=1):
    X_train, X_test = X.iloc[train_idx], X.iloc[test_idx]
    y_train, y_test = y[train_idx], y[test_idx]

    modelo_v2.fit(X_train, y_train)

    y_train_pred = modelo_v2.predict(X_train)
    y_test_pred  = modelo_v2.predict(X_test)

    r2_tr  = r2_score(y_train, y_train_pred)
    r2_te  = r2_score(y_test,  y_test_pred)
    rmse_tr = rmse(y_train, y_train_pred)
    rmse_te = rmse(y_test,  y_test_pred)

    fold_results.append((r2_tr, r2_te, rmse_tr, rmse_te))

    print(f"\nFold {fold}")
    print(f"  Train R2  : {r2_tr:.3f}")
    print(f"  Test  R2  : {r2_te:.3f}")
    print(f"  Train RMSE: {rmse_tr:.3f}")
    print(f"  Test  RMSE: {rmse_te:.3f}")





**Interpretación:**

* **R² de Test entre 0.46 y 0.71** → el modelo realmente está capturando señal, no solo ruido.
* **RMSE de Test ~0.6 a 1.4  unidades** → el error típico es de alrededor de **1 vivienda** en la absorción mensual por proyecto, lo cual es razonable para toma de decisiones.
* El modelo **mejora conforme le damos más historia** (Fold 3 y 4), lo cual es justamente lo que queremos ver en series temporales.

---

### Resumen final de esta sección

Construimos un modelo que:

* Respeta la **naturaleza temporal** de los datos.
* Usa **historia**, **tendencia** y **contexto competitivo**.
* Está **regularizado** para ser robusto, no para “memorizar” el pasado.

---



In [ ]:
# Entrenar modelo final con TODO el histórico
modelo_v2.fit(X, y)




## 3. Importancia global de variables: ¿qué explica realmente la absorción?

Después de entrenar el modelo final con todo el histórico, extraemos la **importancia de variables** desde XGBoost:

El modelo indicó como Top 20 variables:


In [ ]:
# ============================
# IMPORTANCIA GLOBAL DE VARIABLES (XGBoost)
# ============================
pre = modelo_v2.named_steps["preprocess"]
xgb = modelo_v2.named_steps["model"]

# Nombres de features después del OneHot + numéricas
feature_names = pre.get_feature_names_out()
importances = xgb.feature_importances_

imp_df = (
    pd.DataFrame({
        "feature": feature_names,
        "importance": importances
    })
    .sort_values("importance", ascending=False)
    .reset_index(drop=True)
)

# Top 30 variables más importantes
top_n = 10
imp_df.head(top_n)


---

# Como saber si las variables si son importantes 
NIVEL 1 — Análisis descriptivo CONTROLADO (rápido, entendible)

Paso A: Crear la variable binaria

Paso B: Comparar absorción controlando etapa

In [ ]:
df_v["con_juegos"] = (df_v["amen_Juegos_infantiles"] == 1)
df_v.groupby("con_juegos")["Absorcion_prom_mensual"].mean()


Los proyectos con juegos infantiles venden un 96 % más que los proyectos sin juegos infantiles.
Venden más 1.9 veces más.

In [ ]:
df_absorcion = (df_v.groupby(['Fecha', 'con_juegos'], as_index=False)
                      .agg(Absorcion_prom_mensual=('Absorcion_prom_mensual', 'mean'))
                      .round(1))  # opcional: redondear a 1 decimal
import seaborn as sns
import matplotlib.pyplot as plt
import matplotlib.dates as mdates

# Configuración estética global
sns.set_theme(style="whitegrid", context="talk")

plt.figure(figsize=(14, 6))

# Diccionario de colores para asegurar consistencia
# Verde para positivo (tiene juegos), Gris para neutro (no tiene)
colores = {1: "#2ecc71", 0: "#95a5a6"} 
# O si tu columna es booleana/string, ajusta las llaves

# Plot
ax = sns.lineplot(
    data=df_absorcion, 
    x='Fecha', 
    y='Absorcion_prom_mensual', 
    hue='con_juegos', 
    palette=colores,
    marker='o',
    linewidth=2.5,
    markersize=8
)

# Títulos y Etiquetas
plt.title('Impacto de las Áreas de Juegos en la Velocidad de Ventas', fontsize=18, fontweight='bold', pad=20)
plt.ylabel('Absorción (Ventas/Mes)')
plt.xlabel('') # La fecha es obvia, quitamos etiqueta

# Mejorar Leyenda
handles, labels = ax.get_legend_handles_labels()
ax.legend(handles=handles, labels=['Sin Juegos', 'Con Juegos'], title="", loc='upper left', frameon=False)

# Formato de Fechas (Eje X más limpio)
ax.xaxis.set_major_locator(mdates.MonthLocator(interval=3)) # Cada 3 meses
ax.xaxis.set_major_formatter(mdates.DateFormatter('%b-%y')) # Formato: Ene-23
# C. ROTACIÓN: Para que no se empalmen si son muchas
plt.xticks(rotation=45, ha='right')


# Eliminar bordes innecesarios (Spines)
sns.despine(left=True, bottom=True)

plt.tight_layout()
plt.show()

In [ ]:
df_v[df_v["Pct_inventario"].between(0.3, 0.7)].groupby("con_juegos")["Absorcion_prom_mensual"].mean()

A igualdad de etapa del proyecto, Los proyectos con juegos infantiles venden un 125.3 % más que los proyectos sin juegos infantiles.
Venden más del doble (más exactamente, 2.25 veces más, porque 2.14 / 0.95 ≈ 2.25).

Compara solo proyectos en rangos similares:

In [ ]:
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt
import matplotlib.dates as mdates

# 1. PREPARACIÓN DE DATOS (ETL)
# Filtramos solo los registros donde el inventario está entre 30% y 70%
mask_estabilizacion = df_v["Pct_inventario"].between(0.3, 0.7)
df_madurez = df_v[mask_estabilizacion].copy()

# Agrupamos por Fecha y si tiene juegos
df_grafica = (df_madurez.groupby(['Fecha', 'con_juegos'], as_index=False)
              .agg(Absorcion_prom_mensual=('Absorcion_prom_mensual', 'mean')))

# OPCIONAL: Suavizado (Media móvil) para ver mejor la tendencia
# Esto ayuda mucho porque al filtrar perdemos datos y la gráfica puede verse "picuda"
df_grafica = df_grafica.sort_values('Fecha')
df_grafica['Tendencia'] = df_grafica.groupby('con_juegos')['Absorcion_prom_mensual'] \
                                    .transform(lambda x: x.rolling(window=3, min_periods=1).mean())

# 2. VISUALIZACIÓN
sns.set_theme(style="whitegrid", context="talk")
plt.figure(figsize=(14, 7))

# Definimos colores: Verde (Sí juegos) vs Gris (No juegos)
colores = {1: "#27ae60", 0: "#7f8c8d"}

# A) Graficamos las líneas de TENDENCIA (más gruesas y limpias)
sns.lineplot(
    data=df_grafica, 
    x='Fecha', 
    y='Tendencia', 
    hue='con_juegos', 
    palette=colores,
    linewidth=3,
    marker='o'
)

# B) Graficamos un área sombreada ligera para los datos reales (ruido)
# Esto es un truco visual pro: muestra la volatilidad sin ensuciar la línea principal
for cat, color in colores.items():
    subset = df_grafica[df_grafica['con_juegos'] == cat]
    plt.fill_between(subset['Fecha'], 0, subset['Absorcion_prom_mensual'], color=color, alpha=0.05)

# 3. FORMATO Y STORYTELLING
plt.title('Velocidad de Ventas en Etapa de Estabilización\n(Solo proyectos con 30-70% de Inventario)', 
          fontsize=16, fontweight='bold', pad=20)

plt.ylabel('Absorción Promedio (Unidades/Mes)')
plt.xlabel('')

# Eje X - Formato de fechas limpio
plt.gca().xaxis.set_major_formatter(mdates.DateFormatter('%b-%Y'))
plt.gca().xaxis.set_major_locator(mdates.MonthLocator(interval=3))

# C. ROTACIÓN: Para que no se empalmen si son muchas
plt.xticks(rotation=45, ha='right')

# Leyenda personalizada
handles, labels = plt.gca().get_legend_handles_labels()
plt.legend(handles=handles, labels=['Sin Juegos', 'Con Juegos'], 
           title="Amenidades", loc='upper left', frameon=True)

# Anotación explicativa (Contexto)
plt.figtext(0.15, 0.82, "Nota: Se excluyen lanzamientos y saldos finales\npara comparar el desempeño 'orgánico'.", 
            fontsize=10, bbox=dict(facecolor='white', alpha=0.8, edgecolor='gray'))

plt.tight_layout()
sns.despine(left=True)
plt.show()

NIVEL 3 — Contrafactual (nivel maestría / consultoría top)

Aquí respondes:

“¿Qué pasaría si este proyecto NO tuviera juegos infantiles?”

Simulación:

In [ ]:

X_cf = X.copy() 
X_cf["amen_Juegos_infantiles"] = 0 
pred_real = modelo_v2.predict(X) 
pred_cf = modelo_v2.predict(X_cf) 
impacto = pred_real - pred_cf 

mask = (
    (df_v["amen_Juegos_infantiles"] == 1) &
    (df_v["Pct_inventario"].between(0.3, 0.7))
)

impacto[mask].mean()


Cuando el proyecto está en una etapa “comercial activa” (30%–70% de inventario)
y tiene juegos infantiles, la absorción mensual esperada es ≈ +0.12 unidades mayor,
manteniendo todo lo demás constante.

Absorciones promedio ~1.0–1.5

+0.12 = +8% a +15% real, mensual, estructural

Es efecto causal modelado (contrafactual).

Los juegos infantiles generan impacto positivo cuando el proyecto está en su ventana óptima de ventas.

In [ ]:
import shap
import shap 
X_proc = modelo_v2.named_steps["preprocess"].transform(X) 
explainer = shap.Explainer(modelo_v2.named_steps["model"], X_proc) 
shap_values = explainer(X_proc)
shap.dependence_plot(
    "num__amen_Juegos_infantiles",
    shap_values.values,
    X_proc,
    feature_names=feature_names
)


## Variable 2 Delta_avance

¿Qué es exactamente Delta_avance?

Formalmente, en tu modelo:

Delta_avance = Avance_t − Avance_(t−1)


donde:

Avance = Ventas_acumuladas / Número_de_viviendas_planeadas


Es decir:

Delta_avance mide la aceleración o desaceleración del proyecto,
no el nivel absoluto de ventas.

Conceptualmente:

No pregunta “¿cuánto ha vendido?”

Pregunta “¿está acelerando o perdiendo tracción?”

In [ ]:
df_v["Delta_avance"].describe()

In [ ]:
# Crear bins de Delta_avance
df_ctrl = df_v.copy()

q25 = df_v["Delta_avance"].quantile(0.25)  # ≈ 0.00
q50 = df_v["Delta_avance"].quantile(0.50)  # ≈ 0.01
q75 = df_v["Delta_avance"].quantile(0.75)  # ≈ 0.06

df_ctrl["delta_avance_bin"] = pd.cut(
    df_ctrl["Delta_avance"],
    bins=[-1, 0, q50, q75, 1],
    labels=[
        "Retroceso",
        "Avance débil",
        "Avance sólido",
        "Avance acelerado"
    ]
)

# Comparar absorción promedio
df_ctrl.groupby("delta_avance_bin")["Absorcion_prom_mensual"].agg(
    ["mean", "median", "count"]
)


Observaciones clave inmediatas

Relación monotónica perfecta
A mayor Delta_avance, mayor absorción:

0.00 → 0.57 → 1.11 → 2.79


No es binaria, es progresiva
El salto no es “vende / no vende”, sino cuánto más rápido vende.

El efecto es no lineal

Avance débil → sólido: +0.54 unidades

Sólido → acelerado: +1.68 unidades
El mercado premia exponencialmente el momentum.

In [ ]:
import pandas as pd

df_ctrl = df_v.copy()
df_ctrl["Fecha"] = pd.to_datetime(df_ctrl["Fecha"])

# Bins por cuantiles (robusto)
q50 = df_ctrl["Delta_avance"].quantile(0.50)
q75 = df_ctrl["Delta_avance"].quantile(0.75)

df_ctrl["delta_avance_bin"] = pd.cut(
    df_ctrl["Delta_avance"],
    bins=[-1, 0, q50, q75, 1],
    labels=["Retroceso", "Avance débil", "Avance sólido", "Avance acelerado"]
)

# Agregación histórica: mean absorción y cuántos proyectos hay en cada fecha/grupo
df_hist = (df_ctrl
           .groupby(["Fecha", "delta_avance_bin"], as_index=False)
           .agg(
               Absorcion_prom_mensual=("Absorcion_prom_mensual", "mean"),
               n=("Absorcion_prom_mensual", "size")
           ))

# Filtro de estabilidad: mínimo 10 observaciones por fecha/grupo (ajusta 5/10/20)
min_n = 10
df_hist = df_hist[df_hist["n"] >= min_n].copy()

import seaborn as sns
import matplotlib.pyplot as plt
import matplotlib.dates as mdates

sns.set_theme(style="whitegrid", context="talk")

plt.figure(figsize=(14, 6))

ax = sns.lineplot(
    data=df_hist,
    x="Fecha",
    y="Absorcion_prom_mensual",
    hue="delta_avance_bin",
    marker="o",
    linewidth=2.5,
    markersize=7
)

plt.title("Absorción histórica por nivel de avance (Delta_avance)", fontsize=18, fontweight="bold", pad=20)
plt.ylabel("Absorción (Ventas/Mes)")
plt.xlabel("")

ax.xaxis.set_major_locator(mdates.MonthLocator(interval=3))
ax.xaxis.set_major_formatter(mdates.DateFormatter('%b-%y'))
plt.xticks(rotation=45, ha="right")

ax.legend(title="", loc="upper left", frameon=False)
sns.despine(left=True, bottom=True)

plt.tight_layout()
plt.show()



In [ ]:
df_hist2 = df_hist.sort_values(["delta_avance_bin", "Fecha"]).copy()

df_hist2["Abs_3m_smooth"] = (
    df_hist2.groupby("delta_avance_bin")["Absorcion_prom_mensual"]
            .transform(lambda s: s.rolling(3, min_periods=2).mean())
)

plt.figure(figsize=(14, 6))
ax = sns.lineplot(
    data=df_hist2,
    x="Fecha",
    y="Abs_3m_smooth",
    hue="delta_avance_bin",
    linewidth=3
)

plt.title("Absorción histórica (suavizada 3m) por Delta_avance", fontsize=18, fontweight="bold", pad=20)
plt.ylabel("Absorción (Ventas/Mes) - suavizada")
plt.xlabel("")
ax.xaxis.set_major_locator(mdates.MonthLocator(interval=3))
ax.xaxis.set_major_formatter(mdates.DateFormatter('%b-%y'))
plt.xticks(rotation=45, ha="right")
ax.legend(title="", loc="upper left", frameon=False)
sns.despine(left=True, bottom=True)
plt.tight_layout()
plt.show()


In [ ]:

# Controlar por etapa del proyecto (clave)
df_ctrl = df_ctrl[df_ctrl["Pct_inventario"].between(0.3, 0.7)]

df_ctrl.groupby("delta_avance_bin")["Absorcion_prom_mensual"].mean()


In [ ]:
# Controlar también por precio
df_ctrl["precio_bin"] = pd.qcut(
    df_ctrl["Precio_mercado"],
    q=3,
    labels=["Barato", "Mercado", "Caro"]
)

(
    df_ctrl
    .groupby(["precio_bin", "delta_avance_bin"])["Absorcion_prom_mensual"]
    .mean()
    .unstack()
)


In [ ]:
# Validación causal aproximada (contrafactual simple)
X_cf = X.copy()
X_cf["Delta_avance"] = 0

pred_real = modelo_v2.predict(X)
pred_cf   = modelo_v2.predict(X_cf)

impacto_delta = pred_real - pred_cf
impacto_delta.mean()


Manteniendo constantes precio, inventario, zona, amenidades, estacionalidad y momentum, un proyecto con avance positivo vende en promedio ≈ 0.86 viviendas adicionales por mes frente a un escenario donde no hay avance.

Para dimensionarlo:

Absorción media típica por proyecto/mes suele estar alrededor de 0.8 – 1.2

Un impacto de +0.86 implica:

Duplicar la velocidad de ventas en muchos proyectos

O reducir el tiempo de colocación total entre 30% y 50%

Ejemplo intuitivo:

Proyecto sin avance → 1.0 venta/mes

Proyecto con avance → ~1.86 ventas/mes

Económicamente, Delta_avance captura:

Señales de tracción comercial (confianza del mercado)

Momentum psicológico del comprador (“se está vendiendo”)

Activación de referidos y urgencia

Sincronía entre oferta y demanda

Y el modelo ya controló por:

Precio

Inventario

Zona

Amenidades

Estacionalidad

Tendencia histórica

## Primero: ¿qué es exactamente Precio_rel_lag1?

En términos económicos:

Precio_rel_lag1 = Precio del proyecto (t−1) / Precio promedio del mercado (t−1)

Es decir:

< 1 → el proyecto está más barato que el mercado

≈ 1 → está alineado al mercado

> 1 → está por arriba del mercado

Y es lag 1, o sea:
el posicionamiento de precio ANTES del periodo de ventas, no el actual
evita fuga de información



In [ ]:
df_v["Precio_rel_lag1"].describe()


Media ≈ 1.02

➡️ En promedio, los proyectos están alineados al mercado.
Esto es bueno: la variable no está sesgada artificialmente.

🔹 Mediana = 0.89

➡️ Más del 50% de los registros están por debajo del precio de mercado.
Esto es clave:

El mercado de Mazatlán compite por precio, no por sobreprecio.

🔹 Cuartiles (estructura competitiva real)
Rango	Interpretación
< 0.64	Proyectos fuertemente descontados
0.64 – 0.89	Descuento moderado
0.89 – 1.28	Alineados / premium ligero
> 1.28	Sobreprecio claro

➡️ El 75% del mercado está ≤ 1.28,
➡️ El 25% está en sobreprecio fuerte.

Esto explica por qué XGBoost detecta señal:

In [ ]:
df_ctrl = df_v.copy()

df_ctrl["precio_rel_bin"] = pd.cut(
    df_ctrl["Precio_rel_lag1"],
    bins=[0, 0.85, 1.05, 1.30, 10],
    labels=[
        "Descuento agresivo",
        "Descuento leve / competitivo",
        "Precio de mercado",
        "Sobreprecio"
    ]
)

df_ctrl.groupby("precio_rel_bin")["Absorcion_prom_mensual"].agg(
    ["mean", "median", "count"]
)


In [ ]:
X_cf = X.copy()

# Simular precio alineado al mercado
X_cf["Precio_rel_lag1"] = 1.0

pred_real = modelo_v2.predict(X)
pred_cf   = modelo_v2.predict(X_cf)

impacto_precio = pred_real - pred_cf
impacto_precio.mean()



In [ ]:
mask = df_v["Pct_inventario"].between(0.3, 0.7)

impacto_precio[mask].mean()


In [ ]:
import seaborn as sns
import matplotlib.pyplot as plt

plt.figure(figsize=(10,5))
sns.barplot(
    data=df_ctrl,
    x="precio_rel_bin",
    y="Absorcion_prom_mensual",
    estimator="mean",
    ci=None,
    palette="Blues"
)

plt.title("Velocidad de venta según posicionamiento de precio", fontsize=16)
plt.xlabel("Posicionamiento vs mercado")
plt.ylabel("Absorción promedio mensual")
plt.xticks(rotation=20)
plt.tight_layout()
plt.show()


Los proyectos alineados o ligeramente por debajo del precio de mercado presentan la mayor velocidad de absorción. El sobreprecio sostenido reduce significativamente el ritmo de ventas, salvo que exista un avance o propuesta de valor excepcional.

---

# Preguntas a responder 


* ¿Qué características hacen que un proyecto venda más rápido?

Definir subconjunto de control (etapa comparable)

Primero definimos una etapa homogénea del proyecto, por ejemplo:

Inventario relativo entre 30% y 70% (fase media, la más estable)

In [ ]:
df_v['Inventario_relativo'].describe()

In [ ]:
df_ctrl = df_v[
    df_v["Inventario_relativo"].between(0.30, 0.70)
].copy()

print("Registros en etapa controlada:", len(df_ctrl))


| Feature               | Importancia aproximada |
| --------------------- | ---------------------- |
| amen_Pool_Bar         | 0.12                   |
| amen_Cancha_de_Tennis | 0.08                   |
| amen_Gimnasio         | 0.06                   |
| Delta_avance          | 0.06                   |
| Inventario_rel_lag1   | 0.05                   |
| Abs_roll_6            | 0.05                   |
| amen_Cancha_de_futbol | 0.04                   |
| Inventario_relativo   | 0.04                   |
| amen_Dog_park         | 0.04                   |
| Precio_rel_lag1       | 0.03                   |
| amen_Ciclopista       | 0.03                   |
| Mes                   | 0.03                   |
| amen_Elevador         | 0.03                   |
| Abs_roll_3            | 0.03                   |
| Delta_abs_3m          | 0.02                   |
| Precio_mercado        | 0.02                   |
| amen_Mini_golf        | 0.02                   |
| amen_Cine             | 0.02                   |
| Abs_lag_1             | 0.02                   |
| Año                   | 0.02                   |
| Delta_precio          | 0.01                   |

Más que quedarnos con el número exacto, lo importante es interpretar **grupos de variables**:

---

## 3.1. Amenidades “estrella”

Varias amenidades aparecen en los primeros lugares:

* `amen_Pool_Bar`
* `amen_Cancha_de_Tennis`
* `amen_Gimnasio`
* `amen_Cancha_de_futbol`
* `amen_Dog_park`
* `amen_Ciclopista`
* `amen_Elevador`
* `amen_Mini_golf`
* `amen_Cine`

Interpretación:

* No todas las amenidades pesan igual.
* Hay un subconjunto de amenidades que el modelo asocia con **mayor absorción mensual**, una vez controlando por precio, inventario y etapa de vida del proyecto.
* Estas amenidades funcionan como **“aceleradores de ventas”**:

  * Pueden ayudar a defender precios por encima del promedio del mercado (o vender más rápido a mismo precio).

Mensaje:

> “Históricamente, los proyectos que incorporan amenidades tipo *Pool Bar, Cancha de Tennis, Gimnasio, Cine, Ciclopista, Dog Park, etc.*, han mostrado una absorción mensual superior, todo lo demás constante. Es decir, el mercado sí ‘premia’ determinados paquetes de amenidades.”

## 3.2. Ciclo de vida y *momentum* del proyecto 

Estas variables:

- `Abs_roll_6`
- `Abs_roll_3`
- `Abs_lag_1`
- `Delta_abs_3m`
- `Delta_avance`
- `Avance_lag1`

son la forma en la que el modelo “lee” la **historia reciente de ventas** de cada proyecto y determina si el proyecto va:

- **Acelerando**   
- **Estable** 
- **Frenando**   

---

#### 1 Variables base: ¿qué mide cada una?

- `Abs_lag_1`  
  Es la **absorción del periodo anterior** del mismo proyecto  
  > “¿Cuántas viviendas estaba vendiendo el proyecto en el último corte?”

- `Abs_roll_3`  
  Promedio de las **últimas 3 absorciones** (3 cortes anteriores, suavizado).  
  > “En promedio, ¿cuánto venía vendiendo en el corto plazo?”

- `Abs_roll_6`  
  Promedio de las **últimas 6 absorciones**.  
  > “En promedio, ¿cómo ha sido la absorción en el mediano plazo?”

- `Avance_ventas`  
  Porcentaje vendido del proyecto:  
  \[
  Avance\_ventas = \frac{Ventas\_acumuladas}{Numero\_de\_viviendas\_planeadas}
  \]  

- `Avance_lag1`  
  El **avance de ventas en el periodo anterior**.  

- `Delta_abs_3m`  
  En el código se definió como:

  ```python
  Delta_abs_3m = Abs_roll_3 - Abs_lag_1
  ```
  Compara el **promedio de los últimos 3 periodos** contra el **último periodo**.

- `Delta_avance`
  ```python
  Delta_avance = Avance_ventas - Avance_lag1
  ```
  Es el **cambio en el % vendido del proyecto** entre el corte anterior y el actual.

---

####  ¿Cómo sé si un proyecto va acelerando o frenando?

##### a) Comparando `Abs_roll_3` y `Abs_roll_6`

Aquí comparamos corto vs mediano plazo:

* Si:

  [
  Abs_roll_3 > Abs_roll_6
  ]

   **El proyecto viene vendiendo mejor en el corto plazo** que en el mediano.
  Esto indica **aceleración**: las ventas recientes están por encima de su propia historia.

* Si:

  [
  Abs_roll_3 ~ approx Abs_roll_6
  ]

   El proyecto está **estable**, su ritmo reciente se parece al histórico.

* Si:

  [
  Abs_roll_3 < Abs_roll_6
  ]

   El corto plazo está **por debajo del histórico**, el proyecto **se está enfriando**.

**Ejemplo numérico:**

* Caso A (acelerando):

  * `Abs_roll_6 = 3.0` viviendas/mes
  * `Abs_roll_3 = 4.5` viviendas/mes
    ⇒ El corto plazo (4.5) está **por encima** del mediano (3.0) → **aceleración clara**.

* Caso B (enfriando):

  * `Abs_roll_6 = 5.0`
  * `Abs_roll_3 = 3.5`
    ⇒ El corto plazo está **por debajo** del histórico → **el proyecto perdió fuerza**.

---

##### b) Cómo leer `Delta_abs_3m` (¡ojo con el signo!)

En el código:

```python
Delta_abs_3m = Abs_roll_3 - Abs_lag_1
```

* `Abs_roll_3` = promedio de absorción de los últimos 3 periodos (historia reciente).
* `Abs_lag_1` = absorción del **último periodo**.

Entonces:

* Si `Delta_abs_3m > 0`
  → El **promedio de 3 meses es MAYOR que el último mes**.
  → El último corte fue **peor** que la media reciente.
  Interpretación: **el proyecto se está frenando**.

* Si `Delta_abs_3m < 0`
  → El **último mes fue MEJOR que el promedio reciente**.
  Interpretación: **el proyecto se está acelerando**.

* Si `Delta_abs_3m ≈ 0`
  → El último mes está en línea con su promedio de 3 meses.
  Interpretación: **ritmo estable**.

**Ejemplos:**

1. Proyecto A

   * `Abs_roll_3 = 4.0` viv/mes
   * `Abs_lag_1 = 6.0` viv/mes

   ```text
   Delta_abs_3m = 4.0 - 6.0 = -2.0  (< 0)
   ```

   → El último mes (6) estuvo **muy por encima** del promedio (4).
   → **Proyecto acelerado**.

2. Proyecto B

   * `Abs_roll_3 = 5.0`
   * `Abs_lag_1 = 3.0`

   ```text
   Delta_abs_3m = 5.0 - 3.0 = 2.0  (> 0)
   ```

   → El último mes (3) fue **peor** que su promedio (5).
   → **Proyecto frenándose**.

---

##### c) Cómo leer `Delta_avance` y `Avance_lag1`

* `Avance_lag1` te dice **en qué etapa de vida iba el proyecto en el corte anterior**:

  * `Avance_lag1` entre 0.0 y 0.30 → **Etapa temprana** (lanzamiento).
  * Entre 0.30 y 0.70 → **Etapa media** (proyecto consolidado).
  * Mayor a 0.70 → **Etapa madura** (ya casi vendido, quedan “las últimas unidades”).

* `Delta_avance = Avance_ventas - Avance_lag1` mide **qué tanto avanzó el proyecto en % de ventas** desde el corte anterior.

  * `Delta_avance` grande y positivo → el proyecto **avanzó fuerte en ventas** en este periodo.
  * `Delta_avance` pequeño → se vendió poco en % respecto al inventario total.
  * `Delta_avance` casi 0 en proyectos muy maduros (avance > 80%) → indica **fase final**, casi sin inventario atractivo.

**Ejemplos:**

1. Proyecto C (en crecimiento sano):

   * Mes anterior: `Avance_lag1 = 0.20` (20% vendido)
   * Mes actual: `Avance_ventas = 0.28` (28% vendido)

   ```text
   Delta_avance = 0.28 - 0.20 = 0.08  → +8% del proyecto vendido en un periodo
   ```

   → Buen *momentum*: está avanzando fuerte en porcentaje del proyecto.

2. Proyecto D (ya maduro, se está agotando):

   * Mes anterior: `Avance_lag1 = 0.82`
   * Mes actual: `Avance_ventas = 0.84`

   ```text
   Delta_avance = 0.84 - 0.82 = 0.02
   ```

   → Aunque todavía vende algo, el avance es pequeño, típico de **fase final** (quedan pocas unidades y quizá las menos atractivas).

---

#### 3️¿Cuándo consideramos que el proyecto está “bien”?

No es una regla rígida, pero para lectura ejecutiva puedes usar algo así:

* **Proyecto Acelerado** 

  * `Delta_abs_3m < 0`  **y**
  * `Abs_roll_3 ≥ Abs_roll_6`  **y/o**
  * `Delta_avance` ≥ 0.05 (incremento ≥ 5 puntos porcentuales del proyecto en un periodo)

* **Proyecto Estable** 

  * `Delta_abs_3m` cerca de 0 (entre -0.5 y +0.5, por ejemplo)
  * `Abs_roll_3 ≈ Abs_roll_6`
  * `Delta_avance` moderado (2–5 puntos porcentuales).

* **Proyecto Frenado / Enfriándose** 

  * `Delta_abs_3m > 0` (último mes peor que su promedio reciente)
  * `Abs_roll_3 < Abs_roll_6`
  * `Delta_avance` muy bajo (< 0.02), sobre todo si el avance total aún es bajo (ej. < 50%).

Estas reglas son **criterios de interpretación**, no límites matemáticos rígidos, pero sirven para:

* Armar semáforos (verde / amarillo / rojo).
* Explicar a dirección por qué un proyecto se considera en “buena forma” o “en enfriamiento”.

Mensaje:

> “La velocidad actual de ventas no es aleatoria: depende fuertemente de la trayectoria reciente de cada proyecto. El modelo detecta que el ‘momentum’ (historia de absorción y avance de ventas) es una de las piezas clave para explicar por qué algunos proyectos se mantienen fuertes y otros se van enfriando.”

---

## 3.3. Contexto competitivo: inventario y precio relativo

Aquí destacan:

* `Inventario_relativo`
* `Inventario_rel_lag1`
* `Precio_rel_lag1`
* `Precio_mercado`
* `Delta_precio`

Lo que nos dicen:

* `Inventario_relativo` / `Inventario_rel_lag1`:

  * Miden qué % del inventario total del mercado representa ese proyecto.
  * Un proyecto que concentra una porción muy grande de la oferta puede competir de forma distinta a uno que es “pequeño” comparado con la oferta total.
  * También indica si el mercado está muy saturado o no.

* `Precio_rel_lag1` y `Precio_mercado`:

  * No importa solo el nivel de precio, sino **cómo estás posicionado vs el promedio del mercado**.
  * Proyectos demasiado caros vs mercado tienden a tener absorción menor (salvo que estén ultra diferenciados).

* `Delta_precio`:

  * Cambios de precio (subidas o descuentos) tienen impacto directo en la absorción.
  * Si subes precio muy fuerte en poco tiempo, el modelo aprende que eso puede frenar el ritmo de ventas.

Mensaje ejecutivo:

> “La absorción no depende solo del proyecto en sí, sino de cómo se posiciona frente a su competencia directa en cada momento: qué porcentaje de la oferta representa, qué tan arriba o abajo está su precio relativo y cómo han cambiado esos precios recientemente.”

---

## 3.4. Calendario y estacionalidad

Aparecen también:

* `Mes`
* `Año`

Esto indica:

* El modelo detecta **patrones de estacionalidad** (meses donde se vende mejor o peor).

---

## 3.5. Conclusión

En conjunto, el modelo nos dice que la absorción mensual de los proyectos verticales en Mazatlán se explica principalmente por:

1. **Amenidades clave**
   – Cierto paquete de amenidades (Pool Bar, Tennis, Gimnasio, Cine, etc.) se asocia consistentemente con mayor velocidad de ventas.

2. **Momentum del proyecto**
   – La trayectoria de absorción de los últimos meses y el avance de ventas acumuladas explican una gran parte del comportamiento actual.

3. **Posicionamiento competitivo**
   – Precio relativo, inventario relativo y cambios recientes de precio condicionan fuertemente cuán rápido se absorbe el producto.

4. **Factor temporal**
   – Existen meses y años donde, en general, la demanda ha sido más fuerte o más débil, y el modelo lo captura.

Este análisis no solo sirve para predecir, sino para **tomar decisiones**:

* Definir qué amenidades priorizar en futuros desarrollos.
* Ajustar precios considerando el **precio relativo**, no solo el costo interno.
* Monitorear momentum y anticipar cuándo un proyecto puede necesitar ajustes comerciales.
* Evaluar si un proyecto nuevo entra a un mercado con demasiada oferta activa o con espacio para captar demanda.



In [ ]:
# ============================
import shap

# ============================
# 1) Entrenamos modelo final (si no está entrenado)
# ============================
modelo_v2.fit(X, y)

pre = modelo_v2.named_steps["preprocess"]
xgb = modelo_v2.named_steps["model"]

# ============================
# 2) Seleccionar el último periodo
# ============================

# Opción A: exactamente la última fecha disponible
ultima_fecha = df_v["Fecha"].max()
mask_ult = df_v["Fecha"] == ultima_fecha

# Opción B (más robusta): últimos 3 meses
# ultima_fecha = df_v["Fecha"].max()
# cutoff = ultima_fecha - pd.DateOffset(months=3)
# mask_ult = df_v["Fecha"] >= cutoff

X_ult = X.loc[mask_ult]

print("Filas en el último periodo:", len(X_ult))

# ============================
# 3) Transformar X_ult como lo ve el modelo
# ============================

X_ult_trans = pre.transform(X_ult)
feature_names = pre.get_feature_names_out()

# ============================
# 4) SHAP values para LightGBM/XGBoost
# ============================
explainer = shap.TreeExplainer(xgb)
shap_values = explainer.shap_values(X_ult_trans)

# Importancia media absoluta en el último periodo
shap_abs_mean = np.abs(shap_values).mean(axis=0)

shap_df = (
    pd.DataFrame({
        "feature": feature_names,
        "shap_abs_mean": shap_abs_mean
    })
    .sort_values("shap_abs_mean", ascending=False)
)

print("\nTop 25 variables más influyentes en el ÚLTIMO PERIODO:")
print(shap_df.head(25))


## Resumen  
**Variables que más influyen en la absorción en el último periodo**  
### (Top 25 variables por importancia con SHAP)

El modelo identifica cuáles variables tuvieron **mayor influencia real** en explicar la absorción mensual de los proyectos en el **periodo más reciente**.  
Esto nos permite entender **qué está moviendo el mercado hoy** y por qué algunos proyectos venden más que otros.

---

## 1. Dinámica de ventas y ciclo de vida del proyecto  
Las variables *más determinantes* provienen del **momentum del proyecto** y su etapa dentro del ciclo comercial.

### Variable #1: `Delta_avance` (0.73)
- Es la **más influyente por mucho**.  
- Mide qué tanto creció el porcentaje vendido del proyecto desde el periodo anterior.
- Si subió fuerte → el proyecto está **acelerado** (mayor demanda / buenas unidades disponibles).  
- Si subió poco → el proyecto entra en fase **estable**.  

> **Interpretación:** Los proyectos no venden por casualidad; venden cuando están en un momento de inercia positiva. El ritmo reciente de avance es el principal predictor de las ventas futuras.

###  `Abs_roll_6` (0.15) y `Abs_roll_3` (0.07)
Promedios móviles que capturan tendencia de ventas:
- `Abs_roll_6`: desempeño histórico de mediano plazo.  
- `Abs_roll_3`: tendencia reciente (últimos 3 cortes).  

> Si el corto plazo > mediano → aceleración.  
> Si el corto plazo < mediano → enfriamiento.

###  `Abs_lag_1` (0.01)
Refuerza el concepto:  
> “Como vendiste el mes pasado, tiendes a vender este mes… salvo que haya un cambio fuerte en precio o inventario.”

---

##  2. Inventario relativo: posición frente al mercado  
Variables clave:

- `Inventario_rel_lag1` (0.25)  
- `Inventario_relativo` (0.06)  
- `Pct_inv_lag1` (0.03)

Estas variables comparan **cuánto inventario tiene el proyecto vs. todo el mercado**.

- Mucho inventario relativo → más competencia interna → absorción más baja.  
- Poco inventario relativo → “escasez” → más ventas.

> **La absorción** no depende del inventario absoluto del proyecto, sino de su **peso relativo dentro de la oferta disponible**.

## 3. Precio y competitividad  
Variables como:

- `Precio_mercado` (0.03)  
- `Precio_lag1` (0.01)  
- `Precio_relativo` (0.01)  
- `Precio_rel_lag1` (0.01)  
- `Delta_precio` (0.01)

explican cómo la absorción responde a:

- cambios de precio,  
- posición competitiva frente al mercado,  
- si el proyecto está más caro o más barato que sus competidores.

> **Insight:** El mercado responde más a **cambios de precio** que al precio absoluto.

---

## 4. Zona y atributos estructurales  
Variables con menor peso, pero relevantes:

- `Zona_CUM` (0.02)  
- `Zona_Cerritos ciudad` (0.01)  

> Las zonas importan, pero hoy pesan **mucho menos que la dinámica interna del proyecto**.

También aparece:

- `M2_promedio` (0.01)  
- `Cajones_estacionamientos` (0.11)  
- Amenidades como `Elevador` (0.02), `Cine` (0.01), `Gimnasio` (0.01)

Las amenidades sí tienen impacto, pero en este periodo fueron **menos determinantes** que el momentum y la relación precio-inventario.

---

## 5. ¿Qué significa esto para la estrategia comercial?

### Los 3 motores reales que hoy explican la absorción:
1. **Momentum del proyecto**  
   (cómo ha venido vendiendo y en qué etapa está).
2. **Competencia e inventario relativo**  
   (posición dentro de la oferta total del mercado).
3. **Cambios de precio y competitividad**  
   (si el precio cambió o si está desalineado del mercado).


## Conclusión

El modelo revela que **el mercado inmobiliario de Mazatlán funciona por inercia, contexto competitivo y señales de escasez**, más que por atributos físicos del proyecto.

- Si un proyecto está **acelerado**, con bajo inventario relativo, y competitivo en precio → **la absorción será alta**.
- Si un proyecto entra en fase de **enfriamiento**, con inventario abundante y precios desalineados → **la absorción cae**, incluso si es un buen producto.


In [ ]:
import numpy as np
import pandas as pd
from pandas.tseries.offsets import DateOffset

# ============================================================
# 1) PREPARAR ESTADO INICIAL POR PROYECTO A PARTIR DE df_v
# ============================================================

def preparar_estado_inicial(df_v):
    """
    Construye un diccionario con el estado actual de cada proyecto
    usando el último registro disponible en df_v.
    """
    estados = {}
    
    # Año base para Mes_sincronico
    año_min = int(df_v["Año"].min())
    
    # Historial completo de absorción por proyecto
    historiales = (
        df_v.sort_values("Fecha")
            .groupby("Nombre_desarrollo")["Absorcion_prom_mensual"]
            .apply(list)
            .to_dict()
    )
    
    # Última fila por proyecto (estado más reciente)
    df_last = (
        df_v.sort_values("Fecha")
            .groupby("Nombre_desarrollo")
            .tail(1)
            .reset_index(drop=True)
    )
    
    for _, row in df_last.iterrows():
        nombre = row["Nombre_desarrollo"]
        
        estados[nombre] = {
            "nombre": nombre,
            "fecha": row["Fecha"],
            "ventas_acum": row["Ventas_acumuladas"],
            "inventario": row["Inventario_disponible"],
            "viviendas_planeadas": row["Numero_de_viviendas_planeadas"],
            "avance": row["Avance_ventas"],  # ya la calculamos en df_v
            "precio": row["Precio_promedio"],
            "precio_rel": row.get("Precio_relativo", np.nan),
            "inventario_rel": row.get("Inventario_relativo", np.nan),
            "hist_abs": historiales.get(nombre, []),
            # Guardamos TODA la fila como base para copiar columnas estáticas
            "base_row": row.to_dict(),
        }
    
    return estados, año_min


# ============================================================
# 2) FUNCIÓN DE SIMULACIÓN DE UN ESCENARIO
# ============================================================

def simular_escenario_absorcion(
    modelo,
    df_v,
    n_periodos=3,
    freq_meses=3,
    nombre_escenario="Base",
    delta_precio_pct=0.0,
    delta_precio_mercado_pct=0.0,
    factor_inventario_total=1.0,
    delta_competidores=0.0,
    delta_avance_asumido=0.0,
):
    """
    Simula la absorción futura de cada proyecto para n_periodos hacia adelante,
    usando el modelo ya entrenado y df_v como histórico.

    Parámetros clave del escenario:
    - delta_precio_pct: cambio % del precio del proyecto por periodo (ej: 0.05 = +5%).
    - delta_precio_mercado_pct: cambio % del precio promedio del mercado.
    - factor_inventario_total: factor de ajuste del inventario total de mercado (1.2 = +20% oferta).
    - delta_competidores: incremento (o decremento) absoluto en número de competidores.
    - delta_avance_asumido: cuánto asumimos que cambia el avance vs el periodo anterior (puede ser 0).
    """
    
    # 1) Estado inicial por proyecto
    estados, año_min = preparar_estado_inicial(df_v)
    
    # 2) Columnas a excluir para replicar X (las mismas del entrenamiento)
    cols_excluir = [
        "Absorcion_prom_mensual",
        "Fecha",
        "Nombre_desarrollo",
        "Tipo_proyecto",
        # Leakage
        "Ventas_acumuladas",
        "Ventas_periodo",
        "Inventario_disponible",
        "Numero_de_viviendas_planeadas",
        "Precio_promedio",
        "Pct_inventario",
        "Precio_por_M2",
        "Avance_ventas",
    ]
    # x_cols = columnas que realmente entran al modelo
    feature_cols = [c for c in df_v.columns if c not in cols_excluir]
    
    # 3) Fecha inicial (última fecha histórica)
    fecha0 = df_v["Fecha"].max()
    
    resultados = []

    # 4) Simulación horizonte por horizonte
    for h in range(1, n_periodos + 1):
        fecha_h = fecha0 + DateOffset(months=freq_meses * h)
        
        filas_step = []

        # ----- 4.1 Construimos las filas de features para CADA proyecto -----
        for nombre, st in estados.items():
            base = st["base_row"].copy()  # copiamos todas las columnas históricas
            
            # Actualizamos fecha y variables temporales
            base["Fecha"] = fecha_h
            base["Año"] = fecha_h.year
            base["Mes"] = fecha_h.month
            base["Trimestre"] = (fecha_h.month - 1) // 3 + 1
            base["Mes_sincronico"] = (fecha_h.year - año_min) * 12 + fecha_h.month
            base["Mes_sin"] = np.sin(2 * np.pi * fecha_h.month / 12)
            base["Mes_cos"] = np.cos(2 * np.pi * fecha_h.month / 12)
            
            # HISTORIAL DE ABSORCIÓN
            hist = st["hist_abs"]
            if len(hist) >= 1:
                abs_lag_1 = hist[-1]
            else:
                abs_lag_1 = 0.0
            
            base["Abs_lag_1"] = abs_lag_1
            
            if len(hist) >= 2:
                base["Abs_roll_3"] = np.mean(hist[-3:]) if len(hist) >= 3 else np.mean(hist)
            else:
                base["Abs_roll_3"] = abs_lag_1  # fallback
            
            if len(hist) >= 3:
                base["Abs_roll_6"] = np.mean(hist[-6:]) if len(hist) >= 6 else np.mean(hist)
            else:
                base["Abs_roll_6"] = base["Abs_roll_3"]
            
            # AVANCE E INVENTARIO (LAGS)
            base["Avance_lag1"] = st["avance"]
            pct_inv_lag1 = (
                st["inventario"] / st["viviendas_planeadas"]
                if st["viviendas_planeadas"] > 0
                else 0.0
            )
            base["Pct_inv_lag1"] = pct_inv_lag1
            
            # PRECIO DEL PROYECTO
            precio_prev = st["precio"]
            precio_h = precio_prev * (1 + delta_precio_pct)
            base["Precio_promedio"] = precio_h
            base["Precio_lag1"] = precio_prev
            
            # Delta_avance: asumimos escenario (por defecto 0 = ritmo similar)
            base["Delta_avance"] = delta_avance_asumido
            
            # Guardamos nombre de proyecto
            base["Nombre_desarrollo"] = nombre
            
            filas_step.append(base)
        
        df_step = pd.DataFrame(filas_step)
        
        # ----- 4.2 Agregados de mercado (precio e inventario relativos) -----
        # Precio de mercado para este periodo (con ajuste de escenario)
        precio_mercado_h = df_step["Precio_promedio"].mean() * (1 + delta_precio_mercado_pct)
        df_step["Precio_mercado"] = precio_mercado_h
        
        # Precio relativo y su lag
        for idx, row in df_step.iterrows():
            nombre = row["Nombre_desarrollo"]
            precio_rel_h = row["Precio_promedio"] / precio_mercado_h if precio_mercado_h > 0 else 1.0
            df_step.at[idx, "Precio_relativo"] = precio_rel_h
            
            prev_rel = estados[nombre].get("precio_rel", precio_rel_h)
            df_step.at[idx, "Precio_rel_lag1"] = prev_rel
        
        # Inventario total de mercado: suma de inventarios actuales * factor
        inventario_total_h = sum(st["inventario"] for st in estados.values()) * factor_inventario_total
        df_step["Inventario_total"] = inventario_total_h
        
        # Inventario relativo actual y su lag
        for idx, row in df_step.iterrows():
            nombre = row["Nombre_desarrollo"]
            st = estados[nombre]
            inv_rel_h = (
                st["inventario"] / inventario_total_h
                if inventario_total_h > 0
                else 0.0
            )
            df_step.at[idx, "Inventario_relativo"] = inv_rel_h
            
            prev_inv_rel = st.get("inventario_rel", inv_rel_h)
            df_step.at[idx, "Inventario_rel_lag1"] = prev_inv_rel
        
        # Competidores ese mes (aproximación: proyectos activos + ajuste)
        n_comp = len(estados) + delta_competidores
        df_step["Competidores_mes"] = max(n_comp, 1)
        
        # Deltas derivados:
        df_step["Delta_precio"] = df_step["Precio_promedio"] - df_step["Precio_lag1"]
        df_step["Delta_abs_3m"] = df_step["Abs_roll_3"] - df_step["Abs_lag_1"]
        # Delta_avance ya lo pusimos por escenario
        
        # Eliminamos la variable target si viene arrastrada
        if "Absorcion_prom_mensual" in df_step.columns:
            df_step["Absorcion_prom_mensual"] = np.nan
        
        # ----- 4.3 Predicción con el modelo -----
        X_step = df_step[feature_cols]
        y_pred = modelo.predict(X_step)
        
        # ----- 4.4 Actualizar estados y registrar resultados -----
        for i, row in df_step.iterrows():
            nombre = row["Nombre_desarrollo"]
            pred_abs = max(y_pred[i], 0.0)  # no permitimos absorción negativa
            
            st = estados[nombre]
            
            # Ajustamos absorción a inventario disponible
            absorcion_efectiva = min(pred_abs, st["inventario"])
            
            # Actualizar historial de absorción
            st["hist_abs"].append(absorcion_efectiva)
            
            # Actualizar ventas acumuladas e inventario
            st["ventas_acum"] += absorcion_efectiva
            st["inventario"] = max(st["inventario"] - absorcion_efectiva, 0.0)
            
            # Actualizar avance
            if st["viviendas_planeadas"] > 0:
                st["avance"] = st["ventas_acum"] / st["viviendas_planeadas"]
            else:
                st["avance"] = 0.0
            
            # Actualizar precio y relativos en el estado
            st["precio"] = row["Precio_promedio"]
            st["precio_rel"] = row["Precio_relativo"]
            st["inventario_rel"] = row["Inventario_relativo"]
            st["fecha"] = fecha_h
            
            # Guardar resultados de este proyecto en este horizonte
            resultados.append({
                "Escenario": nombre_escenario,
                "Periodo_h": h,
                "Fecha": fecha_h,
                "Nombre_desarrollo": nombre,
                "Absorcion_predicha": float(absorcion_efectiva),
                "Inventario_sim": float(st["inventario"]),
                "Avance_ventas_sim": float(st["avance"]),
                "Precio_sim": float(st["precio"]),
                "Precio_rel_sim": float(st["precio_rel"]),
                "Inventario_rel_sim": float(st["inventario_rel"]),
                "Competidores_mes": float(df_step.loc[i, "Competidores_mes"]),
            })
    
    df_resultados = pd.DataFrame(resultados)
    return df_resultados


In [ ]:
# Escenario 1: Base
escenario_base = simular_escenario_absorcion(
    modelo=modelo_v2,
    df_v=df_v,
    n_periodos=3,          # 3 cortes futuros
    freq_meses=3,          # si tus cortes son trimestrales (cada 3 meses)
    nombre_escenario="Base - precio constante",
    delta_precio_pct=0.0,          # precio del proyecto se mantiene
    delta_precio_mercado_pct=0.0,  # mercado estable
    factor_inventario_total=1.0,   # oferta total similar
    delta_competidores=0,          # mismos proyectos activos
    delta_avance_asumido=0.0       # asumimos mismo ritmo de avance
)

escenario_base.head()


In [ ]:
escenario_base.groupby(["Periodo_h"]).agg({
    "Absorcion_predicha": "mean"})

In [ ]:
#Escenario 2: Subir precio 5% por corte
escenario_subida = simular_escenario_absorcion(
    modelo=modelo_v2,
    df_v=df_v,
    n_periodos=3,
    freq_meses=3,
    nombre_escenario="Subir precio +5% por corte",
    delta_precio_pct=0.05,         # +5% precio proyecto
    delta_precio_mercado_pct=0.0,  # mercado se mantiene
    factor_inventario_total=1.0,
    delta_competidores=0,
    delta_avance_asumido=0.0
)
escenario_subida

In [ ]:
escenario_subida.groupby(["Periodo_h"]).agg({
    "Absorcion_predicha": "mean"})

In [ ]:
# Escenario 3: Promoción (-5% precio) + más competencia
escenario_promo_competencia = simular_escenario_absorcion(
    modelo=modelo_v2,
    df_v=df_v,
    n_periodos=3,
    freq_meses=3,
    nombre_escenario="Promoción -5% + más competencia",
    delta_precio_pct=-0.05,        # bajamos 5% el precio
    delta_precio_mercado_pct=0.0,  # mercado no baja
    factor_inventario_total=1.2,   # 20% más inventario total (más oferta)
    delta_competidores=3,          # 3 proyectos adicionales competidores
    delta_avance_asumido=0.0
)
escenario_promo_competencia

In [ ]:
escenario_promo_competencia.groupby(["Periodo_h"]).agg({
    "Absorcion_predicha": "mean"})

## Modelo 2

In [ ]:

from lightgbm import LGBMRegressor

# ============================================================
# DATASET DE MODELADO PARA VERTICAL: Y vs X_int (mejorado)
# ============================================================

df_v = ventas_vertical_df.copy()

# Aseguramos tipo fecha
df_v["Fecha"] = pd.to_datetime(df_v["Fecha"])
df_v = df_v[df_v["Absorcion_prom_mensual"].notna()].reset_index(drop=True)

# Orden temporal
df_v = df_v.sort_values("Fecha").reset_index(drop=True)

# ==========================
# 1) VARIABLES TEMPORALES
# ==========================
df_v["Mes"] = df_v["Fecha"].dt.month
df_v["Año"] = df_v["Fecha"].dt.year
df_v["Trimestre"] = df_v["Fecha"].dt.quarter
df_v["Mes_sincronico"] = ((df_v["Año"] - df_v["Año"].min()) * 12) + df_v["Mes"]

# Estacionalidad cíclica mes
df_v["Mes_sin"] = np.sin(2 * np.pi * df_v["Mes"] / 12)
df_v["Mes_cos"] = np.cos(2 * np.pi * df_v["Mes"] / 12)

# ==========================
# 2) VARIABLES DE INVENTARIO Y AVANCE
# ==========================

# % inventario restante en el proyecto
df_v["Pct_inventario"] = df_v["Inventario_disponible"] / df_v["Numero_de_viviendas_planeadas"]

# Avance de ventas (momentum del proyecto)
df_v["Avance_ventas"] = df_v["Ventas_acumuladas"] / df_v["Numero_de_viviendas_planeadas"]

# ==========================
# 3) PRECIO Y INVENTARIO RELATIVOS (vs mercado)
# ==========================

# Precio promedio del mercado por fecha
df_v["Precio_mercado"] = df_v.groupby("Fecha")["Precio_promedio"].transform("mean")
df_v["Precio_relativo"] = df_v["Precio_promedio"] / df_v["Precio_mercado"]

# Inventario total del mercado por fecha
df_v["Inventario_total"] = df_v.groupby("Fecha")["Inventario_disponible"].transform("sum")
df_v["Inventario_relativo"] = df_v["Inventario_disponible"] / df_v["Inventario_total"]

# Competidores activos (proyectos únicos en esa fecha)
df_v["Competidores_mes"] = df_v.groupby("Fecha")["Nombre_desarrollo"].transform("nunique")

# ==========================
# 4) LAGS POR PROYECTO Y ROLLING AVERAGES
# ==========================

# Ordenar por proyecto + fecha para lags y rolling
df_v = df_v.sort_values(["Nombre_desarrollo", "Fecha"]).reset_index(drop=True)

# Lags de absorción por proyecto
df_v["Abs_lag_1"] = df_v.groupby("Nombre_desarrollo")["Absorcion_prom_mensual"].shift(1)
df_v["Abs_lag_2"] = df_v.groupby("Nombre_desarrollo")["Absorcion_prom_mensual"].shift(2)
df_v["Abs_lag_3"] = df_v.groupby("Nombre_desarrollo")["Absorcion_prom_mensual"].shift(3)

# Promedio móvil de absorción (tendencia, no solo último valor)
df_v["Abs_roll_3"] = (
    df_v
    .groupby("Nombre_desarrollo")["Absorcion_prom_mensual"]
    .rolling(window=3, min_periods=1)
    .mean()
    .reset_index(level=0, drop=True)
)

df_v["Abs_roll_6"] = (
    df_v
    .groupby("Nombre_desarrollo")["Absorcion_prom_mensual"]
    .rolling(window=6, min_periods=1)
    .mean()
    .reset_index(level=0, drop=True)
)

# Lags de % inventario y avance
df_v["Pct_inv_lag1"] = df_v.groupby("Nombre_desarrollo")["Pct_inventario"].shift(1)
df_v["Avance_lag1"] = df_v.groupby("Nombre_desarrollo")["Avance_ventas"].shift(1)

# Lags de precio e indicadores relativos
df_v["Precio_lag1"] = df_v.groupby("Nombre_desarrollo")["Precio_promedio"].shift(1)
df_v["Precio_rel_lag1"] = df_v.groupby("Nombre_desarrollo")["Precio_relativo"].shift(1)
df_v["Inventario_rel_lag1"] = df_v.groupby("Nombre_desarrollo")["Inventario_relativo"].shift(1)

# ==========================
# 5) DELTAS (CAMBIOS)
# ==========================

df_v["Delta_precio"] = df_v["Precio_promedio"] - df_v["Precio_lag1"]
df_v["Delta_abs_3m"] = df_v["Abs_roll_3"] - df_v["Abs_lag_1"]
df_v["Delta_avance"] = df_v["Avance_ventas"] - df_v["Avance_lag1"]

# ==========================
# 6) LIMPIAR FILAS CON LAGS INCOMPLETOS
# ==========================

cols_lag_core = [
    "Abs_lag_1", "Abs_lag_2", "Abs_lag_3",
    "Abs_roll_3", "Abs_roll_6",
    "Pct_inv_lag1", "Avance_lag1",
    "Precio_lag1", "Precio_rel_lag1", "Inventario_rel_lag1"
]

df_v = df_v.dropna(subset=cols_lag_core).reset_index(drop=True)

# ==========================
# 7) LIMPIAR AMENIDADES CON VARIANZA BAJA
# ==========================

amen_cols = [c for c in df_v.columns if c.startswith("amen_")]
for col in amen_cols:
    # si menos de 5 proyectos/filas la tienen -> no aporta señal
    if df_v[col].sum() < 5:
        df_v = df_v.drop(columns=[col])

# ==========================
# 8) DEFINIR TARGET Y FEATURES (X, y)
# ==========================

y = df_v["Absorcion_prom_mensual"].values

cols_excluir = [
    # Target
    "Absorcion_prom_mensual",

    # Identificadores / llaves
    "Fecha",
    "Nombre_desarrollo",
    "Tipo_proyecto",

    # Variables que pueden causar fuga de información directa
    "Ventas_acumuladas",
    "Ventas_periodo",
    "Inventario_disponible",
    "Numero_de_viviendas_planeadas",
    "Precio_promedio",
    "Precio_por_M2",
    "Precio_mercado",
    "Inventario_total",
]

X = df_v.drop(columns=[c for c in cols_excluir if c in df_v.columns])

# ==========================
# 9) DEFINIR TIPOS: NUMÉRICAS Y CATEGÓRICAS
# ==========================

numeric_features = X.select_dtypes(include=[np.number]).columns.tolist()
categorical_features = X.select_dtypes(include=["object", "category"]).columns.tolist()

for col in categorical_features:
    X[col] = X[col].astype("string").fillna("Missing")

# ==========================
# 10) PIPELINE CON LIGHTGBM
# ==========================

categorical_transformer = Pipeline([
    ("imputer", SimpleImputer(strategy="most_frequent")),
    ("onehot", OneHotEncoder(handle_unknown="ignore")),
])

preprocess = ColumnTransformer([
    ("cat", categorical_transformer, categorical_features),
    ("num", "passthrough", numeric_features),
])

from lightgbm import LGBMRegressor

lgb_model = LGBMRegressor(
    n_estimators=600,
    learning_rate=0.03,
    max_depth=-1,          # deja que LightGBM encuentre la profundidad óptima
    num_leaves=31,
    subsample=0.8,
    colsample_bytree=0.7,
    reg_lambda=2.0,
    reg_alpha=1.0,
    random_state=42
)

modelo_v2 = Pipeline([
    ("preprocess", preprocess),
    ("model", lgb_model),
])

def rmse(a, b):
    return np.sqrt(mean_squared_error(a, b))

# ==========================
# 11) TIME SERIES CROSS-VALIDATION (4 folds)
# ==========================

n = len(df_v)
n_folds = 4

print("=== Time Series Cross-Validation (4 folds, LightGBM) ===\n")

train_r2_list = []
test_r2_list = []
train_rmse_list = []
test_rmse_list = []

# Usamos ventanas crecientes: cada fold entrena con más historia
for k in range(1, n_folds + 1):
    # fracción de datos para train/test
    train_frac_end = 0.5 + 0.1 * k      # 0.6, 0.7, 0.8, 0.9
    test_frac_end  = train_frac_end + 0.1   # 0.7, 0.8, 0.9, 1.0 (aprox)

    train_end = int(n * train_frac_end)
    test_end  = int(min(n * test_frac_end, n))

    if test_end <= train_end:
        continue  # por si acaso

    X_train = X.iloc[:train_end]
    y_train = y[:train_end]
    X_test  = X.iloc[train_end:test_end]
    y_test  = y[train_end:test_end]

    modelo_v2.fit(X_train, y_train)

    y_train_pred = modelo_v2.predict(X_train)
    y_test_pred  = modelo_v2.predict(X_test)

    r2_tr = r2_score(y_train, y_train_pred)
    r2_te = r2_score(y_test,  y_test_pred)
    rmse_tr = rmse(y_train, y_train_pred)
    rmse_te = rmse(y_test,  y_test_pred)

    train_r2_list.append(r2_tr)
    test_r2_list.append(r2_te)
    train_rmse_list.append(rmse_tr)
    test_rmse_list.append(rmse_te)

    print(f"Fold {k}")
    print(f"  Train R2  : {r2_tr:.3f}")
    print(f"  Test  R2  : {r2_te:.3f}")
    print(f"  Train RMSE: {rmse_tr:.3f}")
    print(f"  Test  RMSE: {rmse_te:.3f}\n")

print("...")
print(f"Train R2 medio  : {np.mean(train_r2_list):.3f}")
print(f"Test  R2 medio  : {np.mean(test_r2_list):.3f}")
print(f"Train RMSE medio: {np.mean(train_rmse_list):.3f}")
print(f"Test  RMSE medio: {np.mean(test_rmse_list):.3f}")

# ==========================
# 12) ENTRENAR MODELO FINAL CON TODO EL HISTÓRICO
# ==========================

modelo_v2.fit(X, y)

print("\nModelo final entrenado con todo el histórico listo para usar en predicciones.")
print(f"Total de filas usadas: {len(df_v)}")
print(f"Features numéricas: {len(numeric_features)}  | Categóricas: {len(categorical_features)}")


In [ ]:
# ============================================================
# DATASET DE MODELADO PARA VERTICAL: Y vs X_int
# ============================================================

df_v = ventas_vertical_df.copy()
df_v["Fecha"] = pd.to_datetime(df_v["Fecha"])
df_v = df_v[df_v["Absorcion_prom_mensual"].notna()].reset_index(drop=True)
df_v = df_v.sort_values("Fecha").reset_index(drop=True)

# VARIABLES TEMPORALES
df_v["Mes"] = df_v["Fecha"].dt.month
df_v["Año"] = df_v["Fecha"].dt.year
df_v["Trimestre"] = df_v["Fecha"].dt.quarter
df_v["Mes_sincronico"] = ((df_v["Año"] - df_v["Año"].min()) * 12) + df_v["Mes"]

# LAGS CORRECTOS POR PROYECTO
df_v["Abs_lag_1"] = df_v.groupby("Nombre_desarrollo")["Absorcion_prom_mensual"].shift(1)
df_v["Abs_lag_2"] = df_v.groupby("Nombre_desarrollo")["Absorcion_prom_mensual"].shift(2)
df_v["Abs_lag_3"] = df_v.groupby("Nombre_desarrollo")["Absorcion_prom_mensual"].shift(3)

df_v["Pct_inventario"] = df_v["Inventario_disponible"] / df_v["Numero_de_viviendas_planeadas"]
df_v["Pct_inv_lag1"] = df_v.groupby("Nombre_desarrollo")["Pct_inventario"].shift(1)

df_v["Precio_lag1"] = df_v.groupby("Nombre_desarrollo")["Precio_promedio"].shift(1)

# LIMPIAR LAGS INCOMPLETOS
df_v = df_v.dropna(subset=["Abs_lag_1","Abs_lag_2","Abs_lag_3","Pct_inv_lag1","Precio_lag1"])

# LIMPIAR AMENIDADES CON VARIANZA BAJA
amen_cols = [c for c in df_v.columns if c.startswith("amen_")]
for col in amen_cols:
    if df_v[col].sum() < 5:
        df_v = df_v.drop(columns=[col])

# DEFINIR TARGET Y FEATURES
y = df_v["Absorcion_prom_mensual"].values

cols_excluir = [
    "Absorcion_prom_mensual",
    "Fecha",
    "Nombre_desarrollo",
    "Tipo_proyecto",
    "Ventas_acumuladas",
    "Ventas_periodo",
    "Inventario_disponible",
    "Numero_de_viviendas_planeadas",
    "Precio_promedio",
    "Pct_inventario",
    "Precio_por_M2",
]

X = df_v.drop(columns=cols_excluir)

# CATEGÓRICAS
numeric_features = X.select_dtypes(include=[np.number]).columns.tolist()
categorical_features = X.select_dtypes(include=["object","category"]).columns.tolist()

for col in categorical_features:
    X[col] = X[col].astype("string").fillna("Missing")

# PIPELINE
categorical_transformer = Pipeline([
    ("imputer", SimpleImputer(strategy="most_frequent")),
    ("onehot", OneHotEncoder(handle_unknown="ignore")),
])

preprocess = ColumnTransformer([
    ("cat", categorical_transformer, categorical_features),
    ("num", "passthrough", numeric_features),
])

xgb_model = XGBRegressor(
    n_estimators=300,
    learning_rate=0.05,
    max_depth=4,
    subsample=0.7,
    colsample_bytree=0.7,
    reg_lambda=1,
    reg_alpha=1,
    objective="reg:squarederror",
    random_state=42
)

modelo_v2 = Pipeline([
    ("preprocess", preprocess),
    ("model", xgb_model)
])

n = len(df_v)
split_idx = int(0.8 * n)

X_train = X.iloc[:split_idx]
X_test  = X.iloc[split_idx:]
y_train = y[:split_idx]
y_test  = y[split_idx:]

modelo_v2.fit(X_train, y_train)

y_train_pred = modelo_v2.predict(X_train)
y_test_pred  = modelo_v2.predict(X_test)

print(f"Train R2 : {r2_score(y_train, y_train_pred):.3f}")
print(f"Test  R2 : {r2_score(y_test,  y_test_pred):.3f}")
print(f"Train RMSE: {rmse(y_train, y_train_pred):.3f}")
print(f"Test  RMSE: {rmse(y_test, y_test_pred):.3f}")


In [ ]:
# IMPORTANCIA DE VARIABLES DEL MODELO XGBOOST
# ============================================================

# Extraer pasos
pre = modelo_v2.named_steps["preprocess"]
xgb = modelo_v2.named_steps["model"]

# Obtener nombres reales después de OneHotEncoding
feature_names = pre.get_feature_names_out()

# Importancia por ganancia (más interpretativa)
importances = xgb.feature_importances_

imp_df = pd.DataFrame({
    "feature": feature_names,
    "importance": importances
}).sort_values("importance", ascending=False)

# Gráfica Top 25 variables más importantes del Modelo V2 (XGBoost)
top_n = 25
top_features = imp_df.head(top_n).sort_values("importance")
top_features


In [ ]:
plt.figure(figsize=(10,12))
plt.barh(top_features["feature"], top_features["importance"], color="green")
plt.title("Top Variables que Explican la Absorción Mensual — Modelo XGBoost V2")
plt.xlabel("Importancia (Gain)")
plt.ylabel("Feature")
plt.grid(True, axis="x")
plt.show()

# Varaibles macro

In [ ]:
# Creditos hipotecarios en Mazatlán
# -------Librerias -------#

import requests
import pandas as pd
import dateparser
import sys
import numpy as np

# Add the directory containing your "Funciones" folder to the system path.
sys.path.append(r"C:\Users\julio\OneDrive\Documentos\Trabajo\Ideas Frescas")

# Now you can import the "Funciones" module (which is the folder)
# and then access the "leer_archivo" function.
from Funciones.Funciones import leer_archivo


# Se descargo la base de datos de la pagina https://sniiv.sedatu.gob.mx/Cubo/financiamiento#
# Con los filtros del año 2022 al 2025
# Estado: Sinaloa
# Municipio: Mazatlán
# Variables Modalidad, Tipo de crédito y mes 
# En el eje y año y mes
# En las columnas tipo de crédito: filtrado por 'Crédito individual'
# En la segunda columna 'modalidad' solo vivienda existntes y viviendas nuevas
# Se descargo el excel, se tranformo y limpio la base de datos para guardarla en la caprte BD_variables macro


# Leer archivo
creditos_hipo_mazatlan_individual = leer_archivo(r"C:\Users\julio\OneDrive\Documentos\Trabajo\Ideas Frescas\Proyectos\REM\BD variables macro\Creditos_hipotecarios_Mazatlán_Diciembre- 2025.csv", hoja=1)

creditos_hipo_mazatlan_individual["Fecha"] = pd.to_datetime(
    creditos_hipo_mazatlan_individual["Fecha"],
    format="%d/%m/%Y"
)

# Mostrar resultado
creditos_hipo_mazatlan_individual.head()




In [ ]:
# # PIB Inegi falla PENDIENTE!!!!!!

# # ---- Como se compone la URL ---- #
# # https://www.inegi.org.mx/app/api/indicadores/desarrolladores/jsonxml/INDICATOR/[IdIndicador]/[Idioma]/[Área Geográfica]/[Recientes]/[Fuente de datos]/[Versión][Token]?type=[Formato]
# '''
# IdIndicador
# El primer paso que se debe realizar para obtener información de la API es seleccionar el indicador e identificar su clave. Esto lo puede realizar consultando el "Constructor de consultas".

# Idioma
# La información está disponible en español [es] e inglés [en].

# Área geográfica
# Puede ser nacional [00], por entidad federativa [99] o por municipio [999], dependiendo de cada indicador.

# Dato más reciente o Serie histórica
# Puede consultarse solo el dato más reciente [true] o la serie histórica completa [false].

# Fuente de datos
# Corresponde a la fuente de diseminación [BISE] o [BIE] de donde se obtendrán los datos consultados.

# Versión
# Con él se identificará la edición [2.0] del servicio de provisión de datos.

# Token
# Para utilizar la API es necesario mandarle un token válido, el cual puede obtener al registrarse aquí.

# Formato
# Se ofrece la información en 3 tipos de formatos: JSON [json], JSONP [jsonp] o XML [xml].
# '''


# Token personal del INEGI
TOKEN = 'ccf9a2b3-64b9-4eb8-f202-a8cd92076d04'

# # Indicador del PIB nacional a precios constantes de 2018 (trimestral)
# INDICADOR_PIB_CONST = 735879  # (Fuente INEGI BIE)

# # Área gragrafica
# ag = '00'  # Nacional

# # URL para obtener el indicador del PIB nacional a precios constantes
# url = f'https://www.inegi.org.mx/app/api/indicadores/desarrolladores/jsonxml/INDICATOR/735879/es/00/false/BIE/2.0/{TOKEN}?type=json'

# response = requests.get(url)
# data = response.json()

# # Extraer valores
# valores = data['Series'][0]['OBSERVATIONS']

# # Convertir a DataFrame
# df_pib = pd.DataFrame(valores)

# # Separar año y trimestre
# df_pib[['anio', 'trimestre']] = df_pib['TIME_PERIOD'].str.split('/', expand=True)

# # Mapear trimestres a fechas representativas
# mes_inicio_trimestre = {
#     '01': '01',  # Q1 → enero
#     '02': '04',  # Q2 → abril
#     '03': '07',  # Q3 → julio
#     '04': '10'   # Q4 → octubre
# }
# # Crear columna de fecha válida
# df_pib['fecha'] = pd.to_datetime(df_pib['anio'] + '-' + df_pib['trimestre'].map(mes_inicio_trimestre) + '-01')

# # Dar Formato de valores númericos
# df_pib['PIB_N'] = pd.to_numeric(df_pib['OBS_VALUE'], errors='coerce')
# # Ordenar las fechas de mas antiguo al más reciente
# df_pib = df_pib[['fecha', 'PIB_N']].sort_values('fecha')


# # Extraer año desde la fecha
# df_pib['anio'] = df_pib['fecha'].dt.year

# # Agrupar por año y sumar PIB trimestral
# df_pib_anual = df_pib.groupby('anio', as_index=False)['PIB_N'].sum()

# # Mostrar resultado
# df_pib_anual.rename(columns={'anio': 'date'}, inplace=True)
# # df_pib_anual.to_csv("Data/pib_anual.csv", index=False)
# df_pib_anual.tail()

In [ ]:
# Tasa de interes de referencia
# ---- Extracción de la tasa objetivo diaria del Banco de México ---- #

token_banxico = '3f1b778eb9764c78aebf314182c78d98f26cc66dfae50d4a5fc61a61f52015f6'

# ID de la serie de tasa objetivo diaria
serie_id = 'SF61745' 

url = f'https://www.banxico.org.mx/SieAPIRest/service/v1/series/{serie_id}/datos'


headers = {'Bmx-Token': token_banxico}

response = requests.get(url, headers=headers)

if response.status_code == 200:
    datos = response.json()
    observaciones = datos['bmx']['series'][0]['datos']
    
    df_tasa = pd.DataFrame(observaciones)
    df_tasa['Fecha'] = pd.to_datetime(df_tasa['fecha'], dayfirst=True)
    df_tasa['Tasa objetivo diaria'] = pd.to_numeric(df_tasa['dato'], errors='coerce')
    df_tasa = df_tasa[['Fecha', 'Tasa objetivo diaria']].sort_values('Fecha')
    #display(df_tasa.tail())
else:
    print("Error en la consulta:", response.status_code)
    print(response.text[:500])


# Asegurarte de que la fecha sea el índice
df_tasa.set_index('Fecha', inplace=True)

# Calcular promedio de tasa por trimestre (fin de trimestre)
df_trimestral_raw = df_tasa.resample('MS').mean()

# Resetear índice si lo necesitas como columna
df_tasa_trimestral = df_trimestral_raw.reset_index()
df_tasa_trimestral.columns = ['Fecha', 'tasa_referencia']


# AGREGAR VARIABLES DE REZAGO (LAG) DE LA TASA DE REFERENCIA
df_tasa_trimestral["tasa_referencia_lag_1"] = df_tasa_trimestral["tasa_referencia"].shift(1)
df_tasa_trimestral["tasa_referencia_lag_2"] = df_tasa_trimestral["tasa_referencia"].shift(2)
df_tasa_trimestral["tasa_referencia_lag_3"] = df_tasa_trimestral["tasa_referencia"].shift(3)


df_tasa_trimestral = df_tasa_trimestral.sort_values("Fecha").reset_index(drop=True)
df_tasa_trimestral.tail()

In [ ]:
# Personas económicamente activas y tasa de desempleo tasa de desempleo
#URL para obtener el personas economicamente activas (PEA) a nivel nacional
url_empleo = f' https://www.inegi.org.mx/app/api/indicadores/desarrolladores/jsonxml/INDICATOR/6200093960/es/00/false/BISE/2.0/{TOKEN}?type=json'

response_empleo = requests.get(url_empleo)
data_empleo = response_empleo.json()

mes_inicio_trimestre = {
    '01': '01',  # Q1 → enero
    '02': '04',  # Q2 → abril
    '03': '07',  # Q3 → julio
    '04': '10'   # Q4 → octubre
}

# Extraer valores
valores_empleo = data_empleo['Series'][0]['OBSERVATIONS']
# Convertir a DataFrame
df_empleo = pd.DataFrame(valores_empleo)
# Separar año y trimestre
df_empleo[['anio', 'trimestre']] = df_empleo['TIME_PERIOD'].str.split('/', expand=True)
# Crear columna de fecha válida
df_empleo['Fecha'] = pd.to_datetime(df_empleo['anio'] + '-' + df_empleo['trimestre'].map(mes_inicio_trimestre) + '-01')
# Dar Formato de valores númericos
df_empleo['PEA'] = pd.to_numeric(df_empleo['OBS_VALUE'], errors='coerce')
# Ordenar las fechas de mas antiguo al más reciente
df_empleo = df_empleo[['Fecha', 'PEA']].sort_values('Fecha')


# URL para obtener el población desempleada a nivel nacional
url_desempleo = f'https://www.inegi.org.mx/app/api/indicadores/desarrolladores/jsonxml/INDICATOR/6200093973/es/00/false/BISE/2.0/{TOKEN}?type=json'

response_desempleo = requests.get(url_desempleo)
data_desempleo = response_desempleo.json()

# Extraer valores
valores_desempleo = data_desempleo['Series'][0]['OBSERVATIONS']
# Convertir a DataFrame
df_desempleo = pd.DataFrame(valores_desempleo)
# Separar año y trimestre
df_desempleo[['anio', 'trimestre']] = df_desempleo['TIME_PERIOD'].str.split('/', expand=True)
# Crear columna de fecha válida
df_desempleo['Fecha'] = pd.to_datetime(df_desempleo['anio'] + '-' + df_desempleo['trimestre'].map(mes_inicio_trimestre) + '-01')
# Dar Formato de valores númericos
df_desempleo['valor'] = pd.to_numeric(df_desempleo['OBS_VALUE'], errors='coerce')
# Ordenar las fechas de mas antiguo al más reciente
df_desempleo = df_desempleo[['Fecha', 'valor']].sort_values('Fecha')

# Unir los DataFrames de empleo y desempleo
df_empleo['desempleo'] = df_desempleo['valor']

# Calcular la tasa de desempleo
df_empleo['tasa_desempleo'] = (df_empleo['desempleo'] / df_empleo['PEA']) * 100



df_empleo["Fecha"] = pd.to_datetime(df_empleo["Fecha"])
df_empleo = df_empleo.sort_values("Fecha").reset_index(drop=True)
df_empleo["Fecha"] = pd.to_datetime(
    df_empleo["Fecha"],
    format="%d/%m/%Y"
)

df_empleo.head()

In [ ]:
# Índice Nacional de Precios al Consumidor (INPC)
# Indicador INPC general base 2018 = 100


# Construir URL para el INPC
url = f'https://www.inegi.org.mx/app/api/indicadores/desarrolladores/jsonxml/INDICATOR/910399/es/00/false/BIE-BISE/2.0/{TOKEN}?type=json'

# Hacer la solicitud
response = requests.get(url)
data = response.json()

# Extraer observaciones
valores = data['Series'][0]['OBSERVATIONS']
df_inpc = pd.DataFrame(valores)

# Separar año y mes
df_inpc[['anio', 'mes']] = df_inpc['TIME_PERIOD'].str.split('/', expand=True)

# Crear columna de fecha
df_inpc['Fecha'] = pd.to_datetime(df_inpc['anio'] + '-' + df_inpc['mes'] + '-01')

# Convertir valores a numérico
df_inpc['INPC'] = pd.to_numeric(df_inpc['OBS_VALUE'], errors='coerce')

# Limpiar columnas y ordenar
df_inpc = df_inpc[['Fecha', 'INPC']].sort_values('Fecha')


df_inpc["Fecha"] = pd.to_datetime(df_inpc["Fecha"])
df_inpc = df_inpc.sort_values("Fecha").reset_index(drop=True)
df_inpc["Fecha"] = pd.to_datetime(
    df_inpc["Fecha"],
    format="%d/%m/%Y"
)

df_inpc.head()



In [ ]:
# DENUE Pendiente PENDIENTE!!!!
import requests
import pandas as pd
from time import sleep


# ==============================
# CONFIGURACIÓN
# ==============================
# Token personal del INEGI
DENUE_TOKEN  = 'ccf9a2b3-64b9-4eb8-f202-a8cd92076d04'

BASE_URL_DENUE = "https://www.inegi.org.mx/app/api/denue/v1/consulta"


def denue_cuantificar_municipio(entidad_clave: str, municipio_clave: str, token: str = DENUE_TOKEN) -> pd.DataFrame:
    """
    Usa el método CUANTIFICAR de la API del DENUE para obtener
    el conteo de unidades económicas en un municipio.

    actividad = "0"  -> todas las actividades económicas
    estrato   = "0"  -> todos los tamaños
    área_geo  = 5 dígitos: 2 entidad + 3 municipio (ej. 25 + 006 = 25006)
    """
    area_geo = f"{entidad_clave}{municipio_clave}"   # ej. "25" + "006" = "25006"
    actividad = "0"
    estrato = "0"

    url = f"{BASE_URL_DENUE}/Cuantificar/{actividad}/{area_geo}/{estrato}/{token.strip()}"
    print("Consultando URL:\n", url)

    try:
        resp = requests.get(url, timeout=30)
        print("Status code:", resp.status_code)
        resp.raise_for_status()
    except requests.exceptions.RequestException as e:
        print("⚠️ Error al llamar a la API DENUE:", e)
        return pd.DataFrame()

    # La salida es JSON: lista de registros [ [id_actividad, clave_area, total] , ... ]
    try:
        data = resp.json()
    except ValueError:
        print("⚠️ La respuesta no es JSON. Primeros 500 caracteres:\n", resp.text[:500])
        return pd.DataFrame()

    # Normalizamos en DataFrame
    df = pd.DataFrame(data, columns=["id_actividad", "area_geografica", "total_establecimientos"])
    return df


# 👉 Ejemplo: Mazatlán, Sinaloa
# df_cuantos_mazatlan = denue_cuantificar_municipio("25", "006")
# print(df_cuantos_mazatlan.head())


def denue_buscar_entidad(condicion: str,
                         entidad_clave: str,
                         reg_ini: int,
                         reg_fin: int,
                         token: str = DENUE_TOKEN) -> pd.DataFrame:
    """
    Usa el método BuscarEntidad:
    /BuscarEntidad/{condicion}/{entidad}/{registro_inicial}/{registro_final}/{token}

    - condicion: palabra(s) a buscar, o "todos"
    - entidad_clave: "01".."32" o "00" para todo el país
    - reg_ini, reg_fin: rango de registros. Ojo con poner números RIDÍCULOS, mejor ir por bloques.
    """
    url = f"{BASE_URL_DENUE}/BuscarEntidad/{condicion}/{entidad_clave}/{reg_ini}/{reg_fin}/{token.strip()}"
    print("Consultando URL:\n", url)

    try:
        resp = requests.get(url, timeout=60)
        print("Status code:", resp.status_code)
        resp.raise_for_status()
    except requests.exceptions.RequestException as e:
        print("⚠️ Error al llamar a la API DENUE:", e)
        return pd.DataFrame()

    try:
        data = resp.json()
    except ValueError:
        print("⚠️ La respuesta no es JSON. Primeros 500 caracteres:\n", resp.text[:500])
        return pd.DataFrame()

    # Data suele venir como lista de dicts
    df = pd.DataFrame(data)
    # Opcional: pasar nombres de columnas a minúsculas
    df.columns = df.columns.str.lower()
    return df


# # 👉 Ejemplo: todos los establecimientos de Morelos (entidad 17)
# df_morelos = denue_buscar_entidad("todos", "17", 1, 1000)
# print(df_morelos.head())
# print("Filas descargadas:", len(df_morelos))


In [ ]:
# Pasajeron aéreos de OMA Mazatlán 
# https://www.oma.aero/es/nuestros-servicios/aviacion-comercial/mazatlan-c/estadisticas-de-pasajeros.php

MESES_MAP = {
    "Enero": 1, "January": 1,
    "Febrero": 2, "February": 2,
    "Marzo": 3, "March": 3,
    "Abril": 4, "April": 4,
    "Mayo": 5, "May": 5,
    "Junio": 6, "June": 6,
    "Julio": 7, "July": 7,
    "Agosto": 8, "August": 8,
    "Septiembre": 9, "September": 9,
    "Octubre": 10, "October": 10,
    "Noviembre": 11, "November": 11,
    "Diciembre": 12, "December": 12,
}

def limpiar_tabla(df, tipo):
    df = df.copy()

    # --- 1. Quitar filas Annual Total ---
    df = df[~df.iloc[:,0].astype(str).str.contains("Annual", case=False)]

    # --- 2. Detectar filas que contienen solo el año ---
    df["EsAño"] = df.iloc[:,0].astype(str).str.fullmatch(r"\d{4}")

    # Crear columna Año propagando hacia abajo
    df["Año"] = df.loc[df["EsAño"], df.columns[0]]
    df["Año"] = df["Año"].ffill()

    # --- 3. Quitar filas que solo tienen el año ---
    df = df[~df["EsAño"]]

    # --- 4. Extraer el mes del texto "Enero / January" ---
    df["MesTexto"] = df.iloc[:,0].str.split("/").str[0].str.strip()
    df["Mes"] = df["MesTexto"].map(MESES_MAP)

    # --- 5. Crear columna Fecha ---
    df["Fecha"] = pd.to_datetime(dict(year=df["Año"].astype(int), month=df["Mes"], day=1))

    # --- 6. Borrar columnas basura ---
    df = df.drop(columns=["EsAño", "MesTexto", "Mes"])

    # --- 7. Pasar a LONG FORMAT ---
    df_long = df.melt(
        id_vars=["Fecha"],
        value_vars=df.columns[1:-1],  # todas menos la columna original del mes y Año
        var_name="Aeropuerto",
        value_name="Pasajeros"
    )

    df_long["Tipo"] = tipo

    return df_long


URL_OMA = "https://www.oma.aero/assets/002/5843.xlsx"
SHEET = 0  # o el nombre de la hoja si lo conoces

def cargar_tablas_oma(url=URL_OMA, sheet_name=SHEET):
    # Leemos toda la hoja sin encabezados para poder cortar por posición
    raw = pd.read_excel(url, sheet_name=sheet_name, header=None)

    # Filas 4 a 368  -> en iloc son 3:368  (fin excluyente)
    fila_ini = 3
    fila_fin = 368

    # Tabla 1: A4:O368  -> columnas A(0) a O(14) => 0:15
    dom = raw.iloc[fila_ini:fila_fin, 0:15].copy()

    # Tabla 2: Q4:AE368 -> Q(16) a AE(30) => 16:31
    intl = raw.iloc[fila_ini:fila_fin, 16:31].copy()

    

    # La primera fila de cada rango es el encabezado
    for df in (dom, intl):
        df.columns = df.iloc[0]          # fila de encabezados
        df.drop(df.index[0], inplace=True)
        df.reset_index(drop=True, inplace=True)

    return dom, intl

dom, intl = cargar_tablas_oma()

# La columna Año /YEAR está en ambas tablas, la copiamos a intl porque en la original estaba mal
intl['AÑO /YEAR'] = dom['AÑO /YEAR']

dom_clean  = limpiar_tabla(dom,  "Pasajeros_Nacionales")
intl_clean = limpiar_tabla(intl, "Pasajeros_Internacionales")


# Tabla final unificada
oma = pd.concat([dom_clean, intl_clean], ignore_index=True)

# Pivotear
oma = oma.pivot_table(
    index=["Fecha", "Aeropuerto"],
    columns="Tipo",
    values="Pasajeros",
    aggfunc="sum"
).reset_index()

# Limpieza de datos
oma = oma[(oma['Aeropuerto'] != 'Año') & (oma['Aeropuerto'] != 'Total')]
oma = oma[oma["Aeropuerto"]=="MZT"]

oma["Fecha"] = pd.to_datetime(oma["Fecha"])
oma = oma.sort_values("Fecha").reset_index(drop=True)
oma["Fecha"] = pd.to_datetime(
    oma["Fecha"],
    format="%d/%m/%Y"
)

oma = oma[[ "Fecha", "Pasajeros_Nacionales", "Pasajeros_Internacionales"]]

columnas = ["Pasajeros_Nacionales", "Pasajeros_Internacionales"]   

oma[columnas] = oma[columnas].apply(pd.to_numeric, errors='coerce')
oma.head()

# Modelo Vertical

In [ ]:
# Preparar datos agregados por tipo de proyecto
# ============================================================

# AFiltro por tipo de proyecto: vertical
ventas_vertical = ventas_con_precio_M2[ventas_con_precio_M2["Tipo_proyecto"] == "Vertical"]

#Se esxcluye Aguamarina Talismán
ventas_vertical = ventas_vertical[ventas_vertical['Nombre_desarrollo']!='Aguamarina Talismán']

# Filtrar por proyectos detenidos 
ventas_vertical = ventas_vertical[ventas_vertical['Ventas_detenidas']==0]

# Se agrupan por fecha
ventas_vertical_agg = (
    ventas_vertical
    .groupby("Fecha")
    .agg(
        # contar desarrollos únicos en esa fecha
        Proyectos_unicos=("Nombre_desarrollo", "nunique"),
        
        # sumar variables
        Ventas_acumuladas=("Ventas_acumuladas", "sum"),
        Ventas_periodo=("Ventas_periodo", "sum"),
        Inventario_disponible=("Inventario_disponible", "sum"),
        Numero_de_viviendas_planeadas=("Numero_de_viviendas_planeadas", "sum"),
        Ventas_detenidas=("Ventas_detenidas", "sum"),
        
        # promediar variables de “ritmo” / “intensidad” / “características”
        Absorcion_prom_mensual_x_proy=("Absorcion_prom_mensual", "mean"),
        Absorcion_prom_mensual_total=("Absorcion_prom_mensual", "sum"),
        Precio_promedio=("Precio_promedio", "mean"),
        M2_promedio=("M2_promedio", "mean"),
        Precio_por_M2=("Precio_por_M2", "mean")
    )
    .reset_index()
)
# ===========================================================
# Solo de prueba para ver la importantancia de variables macro
# ============================================================
ventas_vertical_df= ventas_vertical_agg[["Fecha","Proyectos_unicos", 
                                        "Absorcion_prom_mensual_total",
                                        'Inventario_disponible',
                                        'Numero_de_viviendas_planeadas',
                                        "Precio_promedio",
                                        "M2_promedio",
                                        "Precio_por_M2",
                                    ]].copy()  

# ============================================================
# Hacer el merge por Fecha con creditos_hipo_mazatlan_individual
# ============================================================
ventas_vertical_df = ventas_vertical_df.merge(
    creditos_hipo_mazatlan_individual,
    on="Fecha",
    how="left"
)


# ============================================================
# Hacer el merge por Fecha con df_tasa_trimestral
# ============================================================
ventas_vertical_df = ventas_vertical_df.merge(
    df_tasa_trimestral,
    on="Fecha",
    how="left"
)

# ============================================================
# Hacer el merge por Fecha con df_tasa_trimestral
# ============================================================
# Solo columnas macro que quieres traer
cols_macro = ["Fecha", "PEA", "desempleo", "tasa_desempleo"]

ventas_vertical_df = pd.merge_asof(
    ventas_vertical_df,
    df_empleo[cols_macro],
    on="Fecha",          # columna común
    direction="backward" # usa el último dato <= Fecha de ventas
)


# ============================================================
# Hacer el merge por Fecha con df_tasa_trimestral
# ============================================================
ventas_vertical_df = ventas_vertical_df.merge(
    df_inpc,
    on="Fecha",
    how="left"
)



# ============================================================
# Hacer el merge por Fecha con pasajeros de OMA
# ============================================================
ventas_vertical_df = ventas_vertical_df.merge(
    oma,
    on="Fecha",
    how="left"
)


# Revisar resultado
ventas_vertical_df
 

In [ ]:
df_m = ventas_vertical_df.copy()
df_m["Fecha"] = pd.to_datetime(df_m["Fecha"])
df_m = df_m.sort_values("Fecha").reset_index(drop=True)

target = "Absorcion_prom_mensual_total"

# Opcional: quitar columnas que no sirven para explicar (IDs o duplicadas)
cols_drop = ["Ventas_detenidas"]  # si existe y es todo cero
df_m = df_m.drop(columns=[c for c in cols_drop if c in df_m.columns])

# Quitar filas sin target
df_m = df_m[df_m[target].notna()].reset_index(drop=True)


In [ ]:
import numpy as np
import pandas as pd

# Variables candidatas numéricas (macro + internas agregadas)
num_cols = df_m.select_dtypes(include=[np.number]).columns.tolist()
num_cols = [c for c in num_cols if c != target]

corrs = []
for c in num_cols:
    pearson = df_m[[c, target]].corr(method="pearson").iloc[0,1]
    spearman = df_m[[c, target]].corr(method="spearman").iloc[0,1]
    corrs.append((c, pearson, spearman))

corr_df = (pd.DataFrame(corrs, columns=["variable", "pearson_r", "spearman_r"])
             .sort_values("spearman_r", ascending=False))

# Ver top positivos y top negativos
top_pos = corr_df.head(10)
top_neg = corr_df.tail(10)

print("Top + (relación positiva):")
print(top_pos)
print("\nTop - (relación inversa):")
print(top_neg)


In [ ]:
from sklearn.linear_model import Ridge
from sklearn.preprocessing import StandardScaler
from sklearn.pipeline import Pipeline

X_cols = num_cols

X = df_m[X_cols].copy()
y = df_m[target].values

# estandarizar + Ridge
ridge = Pipeline([
    ("scaler", StandardScaler()),
    ("model", Ridge(alpha=1.0))
])

ridge.fit(X, y)
coefs = ridge.named_steps["model"].coef_

coef_df = (pd.DataFrame({"variable": X_cols, "coef": coefs})
             .sort_values("coef", ascending=False))

print("Coeficientes Ridge (signo = dirección controlada):")
print(coef_df.head(10))
print(coef_df.tail(10))


In [ ]:
import statsmodels.api as sm

# Elige exógenas (macro + internas agregadas)
exog_cols = [
    "Proyectos_unicos",
    "Inventario_disponible",
    "Precio_por_M2",
    "tasa_referencia",
    "tasa_desempleo",
    "INPC",
    "Pasajeros_Nacionales",
    "Pasajeros_Internacionales",
    "Viviendas nuevas",
    "Viviendas existentes"
]
exog_cols = [c for c in exog_cols if c in df_m.columns]

y_ts = df_m.set_index("Fecha")[target]
X_ts = df_m.set_index("Fecha")[exog_cols]

# Modelo base: (p,d,q) simple. Con n=19 no te conviene algo grande.
model = sm.tsa.SARIMAX(
    y_ts,
    exog=X_ts,
    order=(1,0,0),
    seasonal_order=(0,0,0,0),
    enforce_stationarity=False,
    enforce_invertibility=False
)
res = model.fit(disp=False)
print(res.summary())


In [ ]:
from xgboost import XGBRegressor
from sklearn.model_selection import TimeSeriesSplit
from sklearn.metrics import r2_score, mean_squared_error
import numpy as np

X = df_m[exog_cols].copy()
y = df_m[target].values

xgb = XGBRegressor(
    n_estimators=200,
    max_depth=2,
    learning_rate=0.05,
    subsample=0.8,
    colsample_bytree=0.8,
    reg_lambda=5,
    reg_alpha=1,
    min_child_weight=5,
    objective="reg:squarederror",
    random_state=42
)

tscv = TimeSeriesSplit(n_splits=4)
r2s, rmses = [], []

for fold, (tr, te) in enumerate(tscv.split(X), 1):
    xgb.fit(X.iloc[tr], y[tr])
    pred = xgb.predict(X.iloc[te])
    r2s.append(r2_score(y[te], pred))
    rmses.append(np.sqrt(mean_squared_error(y[te], pred)))
    print(f"Fold {fold} R2={r2s[-1]:.3f} RMSE={rmses[-1]:.3f}")

print("R2 medio:", np.mean(r2s), "RMSE medio:", np.mean(rmses))


In [ ]:
def shock_efecto(model, X_base, col, delta):
    X1 = X_base.copy()
    X2 = X_base.copy()
    X2[col] = X2[col] + delta
    
    p1 = model.predict(X1)
    p2 = model.predict(X2)
    return float(np.mean(p2 - p1))

# entrenas el modelo final con TODO (para usarlo en simulación)
xgb.fit(X, y)

for col, delta in [
    ("tasa_referencia", 1.0),            # +1 punto porcentual
    ("tasa_desempleo", 0.5),             # +0.5 puntos
    ("Pasajeros_Nacionales", 10000),      # +10k pasajeros
    ("INPC", 0.1),                       # +0.1 (según tu escala)
]:
    if col in X.columns:
        eff = shock_efecto(xgb, X, col, delta)
        print(f"Efecto promedio de shock {col} (+{delta}): {eff:.3f} absorción total")


In [ ]:
h = 5  # 3 a 5 periodos futuros

df_hist = df_m.copy().set_index("Fecha")

mu = df_hist[exog_cols].pct_change().mean()   # drift promedio
sigma = df_hist[exog_cols].pct_change().std() # volatilidad

last = df_hist[exog_cols].iloc[-1].copy()


In [ ]:
def simular_exog(last_values, mu, sigma, h, n_sims=5000, shocks=None, seed=42):
    """
    shocks: dict con multiplicadores o ajustes por columna
      ejemplo:
        {"tasa_referencia": +0.02}  -> +2% por periodo sobre el drift
        {"Pasajeros_Nacionales": -0.10} -> -10% por periodo (estrés)
    """
    rng = np.random.default_rng(seed)
    shocks = shocks or {}

    sims = []
    for s in range(n_sims):
        path = []
        cur = last_values.copy()

        for t in range(h):
            # crecimiento aleatorio por variable
            g = rng.normal(mu.values, sigma.values)
            g = pd.Series(g, index=mu.index)

            # aplicar shocks del escenario
            for k, v in shocks.items():
                if k in g.index:
                    g[k] = g[k] + v

            # actualizar nivel (evitar negativos con clip si aplica)
            cur = cur * (1 + g)

            # Si hay variables que NO deben ir negativas:
            for col in cur.index:
                cur[col] = max(cur[col], 0)

            path.append(cur.copy())

        sims.append(pd.DataFrame(path))

    # sims -> list de DataFrames h x exog
    return sims


In [ ]:
escenarios = {
    "Base": {},
    "Optimista": {
        "tasa_referencia": -0.05,          # cae más rápido
        "tasa_desempleo":  -0.03,
        "Pasajeros_Nacionales": +0.08,
        "Pasajeros_Internacionales": +0.10,
    },
    "Estres": {
        "tasa_referencia": +0.05,
        "tasa_desempleo":  +0.04,
        "Pasajeros_Nacionales": -0.10,
        "Pasajeros_Internacionales": -0.15,
    }
}


In [ ]:
def predecir_mc(model, sims, exog_cols, future_dates):
    # devuelve matriz [n_sims, h]
    preds = np.zeros((len(sims), len(future_dates)), dtype=float)

    for i, df_path in enumerate(sims):
        df_path.columns = exog_cols
        df_path.index = future_dates
        Xf = df_path[exog_cols]
        preds[i, :] = model.predict(Xf)

    return preds

# Entrena modelo final (XGB o SARIMAX; aquí uso XGB)
xgb.fit(X, y)

last_date = df_hist.index[-1]
future_dates = pd.date_range(last_date + pd.offsets.MonthBegin(3), periods=h, freq="QS")  # trimestral
# Si tu serie es trimestral (abril/julio/oct/ene), ajústalo a tu calendario real.

resultados = {}

for nombre, shocks in escenarios.items():
    sims = simular_exog(last, mu, sigma, h, n_sims=5000, shocks=shocks, seed=42)
    preds = predecir_mc(xgb, sims, exog_cols, future_dates)

    resumen = pd.DataFrame({
        "Fecha": future_dates,
        "mean": preds.mean(axis=0),
        "p10": np.percentile(preds, 10, axis=0),
        "p50": np.percentile(preds, 50, axis=0),
        "p90": np.percentile(preds, 90, axis=0),
    })
    resultados[nombre] = resumen

resultados["Base"]


In [ ]:
# DATASET DE MODELADO PARA VERTICAL: Y vs X_int
# ============================================================

# Copia de trabajo
df_v = ventas_vertical_df.copy()

# Aseguramos tipo fecha
df_v["Fecha"] = pd.to_datetime(df_v["Fecha"])

#  filtrar periodos muy raros:
# df_v = df_v[df_v["Absorcion_prom_mensual"] < 0]

# Eliminamos filas sin target
df_v = df_v[df_v["Absorcion_prom_mensual_total"].notna()].reset_index(drop=True)

# ORDENAMOS POR TIEMPO para respetar la serie
df_v = df_v.sort_values("Fecha").reset_index(drop=True)

# AGREGAR VARIABLES TEMPORALES
df_v["Mes"] = df_v["Fecha"].dt.month
df_v["Año"] = df_v["Fecha"].dt.year
df_v["Trimestre"] = df_v["Fecha"].dt.quarter
df_v["Mes_sincronico"] = (df_v["Fecha"].dt.year - df_v["Fecha"].dt.year.min())*12 + df_v["Fecha"].dt.month

# AGREGAR VARIABLES DE REZAGO (LAG)
df_v["Abs_lag_1"] = df_v["Absorcion_prom_mensual_total"].shift(1)
df_v["Abs_lag_2"] = df_v["Absorcion_prom_mensual_total"].shift(2)
df_v["Abs_lag_3"] = df_v["Absorcion_prom_mensual_total"].shift(3)

# % Inventario restnate
df_v["Pct_inventario"] = df_v["Inventario_disponible"] / df_v["Numero_de_viviendas_planeadas"]


# ---------------------------
# Definir variable objetivo Y
# ---------------------------
y = df_v["Absorcion_prom_mensual_total"].values

# ---------------------------
# Definir matriz de features X
# ---------------------------
# Columnas que NO deben entrar como features
cols_excluir = [
    # Target
    "Absorcion_prom_mensual_total",

    # Identificadores
    "Fecha",

    # Variables que generan leakage
    "Inventario_disponible",
    "Numero_de_viviendas_planeadas",
]


# IMPORTANTE:
# Un modelo que explique absorción sin usar
# variables "resultado" del mismo periodo, puedes EXCLUIR
# algunas de estas:
#   - "Ventas_acumuladas"
#   - "Ventas_periodo"
# Por ahora las dejamos como features explicativas internas,
# pero las puedes comentar aquí si quieres un modelo más "estricto".
# cols_excluir += ["Ventas_acumuladas", "Ventas_periodo"]

X = df_v.drop(columns=cols_excluir)

# Separar numéricas y categóricas
numeric_features = X.select_dtypes(include=[np.number]).columns.tolist()
categorical_features = X.select_dtypes(include=["object", "category"]).columns.tolist()


# ============================================================
# 4. Normalización robusta de categóricas para evitar errores
# ============================================================

for col in categorical_features:
    # Convertimos todo a string (incluidos los NA)
    X[col] = X[col].astype("string")
    
    # Reemplazamos pd.NA por un string 'Missing'
    X[col] = X[col].fillna("Missing")


print("Columnas numéricas:", len(numeric_features))
print("Columnas categóricas:", len(categorical_features))

In [ ]:
# Preprocesamiento para variables categóricas
categorical_transformer = Pipeline(steps=[
    ("imputer", SimpleImputer(strategy="most_frequent")),
    ("onehot", OneHotEncoder(handle_unknown="ignore"))
])

# Ensamblador
preprocess = ColumnTransformer(
    transformers=[
        ("cat", categorical_transformer, categorical_features),
        ("num", "passthrough", numeric_features),
    ]
)

xgb_model = XGBRegressor(
    n_estimators=600,
    learning_rate=0.05,
    max_depth=6,
    subsample=0.9,
    colsample_bytree=0.7,
    objective="reg:squarederror",
    random_state=42,
    n_jobs=-1
)


modelo_v2 = Pipeline(steps=[
    ("preprocess", preprocess),
    ("model", xgb_model)
])


n = len(df_v)
split_idx = int(0.8 * n)

X_train = X.iloc[:split_idx]
X_test  = X.iloc[split_idx:]
y_train = y[:split_idx]
y_test  = y[split_idx:]

print(f"Train: {X_train.shape[0]}  | Test: {X_test.shape[0]}")


modelo_v2.fit(X_train, y_train)

y_train_pred = modelo_v2.predict(X_train)
y_test_pred  = modelo_v2.predict(X_test)

def rmse(a, b):
    return np.sqrt(mean_squared_error(a, b))

print("\n=== Desempeño Modelo V2 (XGBoost) ===")
print(f"Train R2 : {r2_score(y_train, y_train_pred):.3f}")
print(f"Test  R2 : {r2_score(y_test,  y_test_pred):.3f}")
print(f"Train RMSE: {rmse(y_train, y_train_pred):.3f}")
print(f"Test  RMSE: {rmse(y_test, y_test_pred):.3f}")


In [ ]:
df_macro = ventas_vertical_df.dropna(subset=["Absorcion_prom_mensual_total"]).copy()

y_macro = df_macro["Absorcion_prom_mensual_total"].values

cols_excluir = ["Absorcion_prom_mensual_total", "Fecha"]
X_macro = df_macro.drop(columns=cols_excluir)

num_feats = X_macro.select_dtypes(include=[np.number]).columns.tolist()

# Modelo simple (por ejemplo XGBoost o RandomForest solo con numéricas)
from xgboost import XGBRegressor
from sklearn.metrics import r2_score, mean_squared_error

model_macro = XGBRegressor(
    n_estimators=400,
    learning_rate=0.05,
    max_depth=4,
    subsample=0.9,
    colsample_bytree=0.8,
    objective="reg:squarederror",
    random_state=42
)

# Split temporal
n = len(df_macro)
split_idx = int(0.8 * n)
X_train = X_macro.iloc[:split_idx]
X_test  = X_macro.iloc[split_idx:]
y_train = y_macro[:split_idx]
y_test  = y_macro[split_idx:]

model_macro.fit(X_train, y_train)

y_pred_train = model_macro.predict(X_train)
y_pred_test  = model_macro.predict(X_test)

rmse = lambda a,b: np.sqrt(mean_squared_error(a,b))

print("R2 train:", r2_score(y_train, y_pred_train))
print("R2 test :", r2_score(y_test,  y_pred_test))
print("RMSE train:", rmse(y_train, y_pred_train))
print("RMSE test :", rmse(y_test,  y_pred_test))


In [ ]:


# ============================================================
# DATASET FINAL DE MODELADO (Y vs X_int)
# ============================================================

ventas_vertical_df = ventas_vertical.merge(
    vertical_amen,
    on=["Nombre_desarrollo"],
    how="left",
    
)

# Asegurar que ambas sean datetime
ventas_vertical_df["Fecha"] = pd.to_datetime(ventas_vertical_df["Fecha"])
ventas_vertical_df["Fecha_inicio_venta"] = pd.to_datetime(ventas_vertical_df["Fecha_inicio_venta"])

# Calcular meses desde inicio de ventas
ventas_vertical_df["Meses_desde_inicio_ventas"] = (
    (ventas_vertical_df["Fecha"].dt.year - ventas_vertical_df["Fecha_inicio_venta"].dt.year) * 12 +
    (ventas_vertical_df["Fecha"].dt.month - ventas_vertical_df["Fecha_inicio_venta"].dt.month)
)

# Si quieres evitar valores negativos por errores de captura:
ventas_vertical_df["Meses_desde_inicio_ventas"] = ventas_vertical_df["Meses_desde_inicio_ventas"].clip(lower=0)

ventas_vertical_df = ventas_vertical_df.sort_values("Fecha").reset_index(drop=True)

# ===========================================================
# Solo de prueba para ver la importantancia de variables macro
# ============================================================
ventas_vertical_df= ventas_vertical_df[["Fecha","Nombre_desarrollo", 
                                        "Tipo_proyecto",
                                        "Ventas_acumuladas",
                                        "Ventas_periodo",
                                        "Inventario_disponible",
                                        "Numero_de_viviendas_planeadas",
                                        "Absorcion_prom_mensual"]]
ventas_vertical_df  = ventas_vertical.copy()                                        
                                            
# ============================================================
# Hacer el merge por Fecha con creditos_hipo_mazatlan_individual
# ============================================================
ventas_vertical_df = ventas_vertical_df.merge(
    creditos_hipo_mazatlan_individual,
    on="Fecha",
    how="left"
)


# ============================================================
# Hacer el merge por Fecha con df_tasa_trimestral
# ============================================================
ventas_vertical_df = ventas_vertical_df.merge(
    df_tasa_trimestral,
    on="Fecha",
    how="left"
)

# ============================================================
# Hacer el merge por Fecha con df_tasa_trimestral
# ============================================================
# Solo columnas macro que quieres traer
cols_macro = ["Fecha", "PEA", "desempleo", "tasa_desempleo"]

ventas_vertical_df = pd.merge_asof(
    ventas_vertical_df,
    df_empleo[cols_macro],
    on="Fecha",          # columna común
    direction="backward" # usa el último dato <= Fecha de ventas
)


# ============================================================
# Hacer el merge por Fecha con df_tasa_trimestral
# ============================================================
ventas_vertical_df = ventas_vertical_df.merge(
    df_inpc,
    on="Fecha",
    how="left"
)



# ============================================================
# Hacer el merge por Fecha con pasajeros de OMA
# ============================================================
ventas_vertical_df = ventas_vertical_df.merge(
    oma,
    on="Fecha",
    how="left"
)


# Revisar resultado
ventas_vertical_df.tail()



In [ ]:
# DATASET DE MODELADO PARA VERTICAL: Y vs X_int
# ============================================================

# Copia de trabajo
df_v = ventas_vertical_df.copy()

# Aseguramos tipo fecha
df_v["Fecha"] = pd.to_datetime(df_v["Fecha"])

#  filtrar periodos muy raros:
# df_v = df_v[df_v["Absorcion_prom_mensual"] < 0]

# Eliminamos filas sin target
df_v = df_v[df_v["Abs_ciudad"].notna()].reset_index(drop=True)

# ORDENAMOS POR TIEMPO para respetar la serie
df_v = df_v.sort_values("Fecha").reset_index(drop=True)

# AGREGAR VARIABLES TEMPORALES
df_v["Mes"] = df_v["Fecha"].dt.month
df_v["Año"] = df_v["Fecha"].dt.year
df_v["Trimestre"] = df_v["Fecha"].dt.quarter
df_v["Mes_sincronico"] = (df_v["Fecha"].dt.year - df_v["Fecha"].dt.year.min())*12 + df_v["Fecha"].dt.month

# AGREGAR VARIABLES DE REZAGO (LAG)
df_v["Abs_lag_1"] = df_v["Abs_ciudad"].shift(1)
df_v["Abs_lag_2"] = df_v["Abs_ciudad"].shift(2)
df_v["Abs_lag_3"] = df_v["Abs_ciudad"].shift(3)

# % Inventario restnate
df_v["Pct_inventario"] = df_v["Inventario_total"] / df_v["total_unidades_planeadas"]


# ---------------------------
# Definir variable objetivo Y
# ---------------------------
y = df_v["Abs_ciudad"].values

# ---------------------------
# Definir matriz de features X
# ---------------------------
# Columnas que NO deben entrar como features
cols_excluir = [
    # Target
    "Abs_ciudad",

    # Identificadores
    "Fecha",
    # "Nombre_desarrollo",
    # "Tipo_proyecto",

    # Variables que generan leakage
    "Ventas_acumuladas",
    "Ventas_periodo",
    "Inventario_total",
    "total_unidades_planeadas",
]


# IMPORTANTE:
# Un modelo que explique absorción sin usar
# variables "resultado" del mismo periodo, puedes EXCLUIR
# algunas de estas:
#   - "Ventas_acumuladas"
#   - "Ventas_periodo"
# Por ahora las dejamos como features explicativas internas,
# pero las puedes comentar aquí si quieres un modelo más "estricto".
# cols_excluir += ["Ventas_acumuladas", "Ventas_periodo"]

X = df_v.drop(columns=cols_excluir)

# Separar numéricas y categóricas
numeric_features = X.select_dtypes(include=[np.number]).columns.tolist()
categorical_features = X.select_dtypes(include=["object", "category"]).columns.tolist()


# ============================================================
# 4. Normalización robusta de categóricas para evitar errores
# ============================================================

for col in categorical_features:
    # Convertimos todo a string (incluidos los NA)
    X[col] = X[col].astype("string")
    
    # Reemplazamos pd.NA por un string 'Missing'
    X[col] = X[col].fillna("Missing")


print("Columnas numéricas:", len(numeric_features))
print("Columnas categóricas:", len(categorical_features))


In [ ]:
# Preprocesamiento para variables categóricas
categorical_transformer = Pipeline(steps=[
    ("imputer", SimpleImputer(strategy="most_frequent")),
    ("onehot", OneHotEncoder(handle_unknown="ignore"))
])

# Ensamblador
preprocess = ColumnTransformer(
    transformers=[
        ("cat", categorical_transformer, categorical_features),
        ("num", "passthrough", numeric_features),
    ]
)

xgb_model = XGBRegressor(
    n_estimators=600,
    learning_rate=0.05,
    max_depth=6,
    subsample=0.9,
    colsample_bytree=0.7,
    objective="reg:squarederror",
    random_state=42,
    n_jobs=-1
)


modelo_v2 = Pipeline(steps=[
    ("preprocess", preprocess),
    ("model", xgb_model)
])


n = len(df_v)
split_idx = int(0.8 * n)

X_train = X.iloc[:split_idx]
X_test  = X.iloc[split_idx:]
y_train = y[:split_idx]
y_test  = y[split_idx:]

print(f"Train: {X_train.shape[0]}  | Test: {X_test.shape[0]}")


modelo_v2.fit(X_train, y_train)

y_train_pred = modelo_v2.predict(X_train)
y_test_pred  = modelo_v2.predict(X_test)

def rmse(a, b):
    return np.sqrt(mean_squared_error(a, b))

print("\n=== Desempeño Modelo V2 (XGBoost) ===")
print(f"Train R2 : {r2_score(y_train, y_train_pred):.3f}")
print(f"Test  R2 : {r2_score(y_test,  y_test_pred):.3f}")
print(f"Train RMSE: {rmse(y_train, y_train_pred):.3f}")
print(f"Test  RMSE: {rmse(y_test, y_test_pred):.3f}")


In [ ]:
# REAL vs PREDICHO (solo test)
# # ============================================================

# df_pred = df_v.iloc[split_idx:].copy()
# df_pred = df_pred[["Fecha", "Nombre_desarrollo", "Absorcion_prom_mensual"]]

# df_pred["Abs_real"] = y_test
# df_pred["Abs_pred"] = y_test_pred

# df_pred.sort_values("Fecha", inplace=True)
# df_pred.reset_index(drop=True, inplace=True)

# plt.figure(figsize=(14,6))
# plt.plot(df_pred["Fecha"], df_pred["Abs_real"], label="Real", color="blue", linewidth=2)
# plt.plot(df_pred["Fecha"], df_pred["Abs_pred"], label="Predicción", color="orange", linewidth=2)
# plt.title("Absorción Mensual - Real vs Predicho (Test Set)")
# plt.xlabel("Fecha")
# plt.ylabel("Unidades/mes")
# plt.legend()
# plt.grid(True)
# plt.show()



In [ ]:
# IMPORTANCIA DE VARIABLES DEL MODELO XGBOOST
# ============================================================

# Extraer pasos
pre = modelo_v2.named_steps["preprocess"]
xgb = modelo_v2.named_steps["model"]

# Obtener nombres reales después de OneHotEncoding
feature_names = pre.get_feature_names_out()

# Importancia por ganancia (más interpretativa)
importances = xgb.feature_importances_

imp_df = pd.DataFrame({
    "feature": feature_names,
    "importance": importances
}).sort_values("importance", ascending=False)

# Gráfica Top 25 variables más importantes del Modelo V2 (XGBoost)
top_n = 25
top_features = imp_df.head(top_n).sort_values("importance")

plt.figure(figsize=(10,12))
plt.barh(top_features["feature"], top_features["importance"], color="green")
plt.title("Top Variables que Explican la Absorción Mensual — Modelo XGBoost V2")
plt.xlabel("Importancia (Gain)")
plt.ylabel("Feature")
plt.grid(True, axis="x")
plt.show()



In [ ]:
# Gráfica de las Amenidades más influyentes
amen_imp = imp_df[imp_df["feature"].str.contains("amen_", case=False)].copy()
amen_imp = amen_imp.sort_values("importance", ascending=False)

plt.figure(figsize=(10,12))
plt.barh(amen_imp.head(15)["feature"][::-1], amen_imp.head(15)["importance"][::-1])
plt.title("Amenidades más influyentes en la Absorción — Modelo XGBoost")
plt.xlabel("Importancia (Gain)")
plt.grid(True, axis="x")
plt.show()


# Resuemn general por tipo de proyecto

In [ ]:
# Preparar datos agregados por tipo de proyecto
# ============================================================

# AFiltro por tipo de proyecto: vertical
ventas_vertical = ventas_con_precio_M2[ventas_con_precio_M2["Tipo_proyecto"] == "Vertical"]

#Se esxcluye Aguamarina Talismán
ventas_vertical = ventas_vertical[ventas_vertical['Nombre_desarrollo']!='Aguamarina Talismán']

# Filtrar por proyectos detenidos 
ventas_vertical = ventas_vertical[ventas_vertical['Ventas_detenidas']==0]

# Se agrupan por fecha
ventas_vertical_agg = (
    ventas_vertical
    .groupby("Fecha")
    .agg(
        # contar desarrollos únicos en esa fecha
        Proyectos_unicos=("Nombre_desarrollo", "nunique"),
        
        # sumar variables
        Ventas_acumuladas=("Ventas_acumuladas", "sum"),
        Ventas_periodo=("Ventas_periodo", "sum"),
        Inventario_disponible=("Inventario_disponible", "sum"),
        Numero_de_viviendas_planeadas=("Numero_de_viviendas_planeadas", "sum"),
        Ventas_detenidas=("Ventas_detenidas", "sum"),
        
        # promediar variables de “ritmo” / “intensidad” / “características”
        Absorcion_prom_mensual=("Absorcion_prom_mensual", "mean"),
        Absorcion_prom_mensual_total=("Absorcion_prom_mensual", "sum"),
        Precio_promedio=("Precio_promedio", "mean"),
        M2_promedio=("M2_promedio", "mean"),
        Precio_por_M2=("Precio_por_M2", "mean")
    )
    .reset_index()
)

# ============================================================
# Hacer el merge por Fecha con creditos_hipo_mazatlan_individual
# ============================================================
ventas_vertical_df = ventas_vertical_agg.merge(
    creditos_hipo_mazatlan_individual,
    on="Fecha",
    how="left"
)


# ============================================================
# Hacer el merge por Fecha con df_tasa_trimestral
# ============================================================
ventas_vertical_df = ventas_vertical_df.merge(
    df_tasa_trimestral,
    on="Fecha",
    how="left"
)

# ============================================================
# Hacer el merge por Fecha con df_tasa_trimestral
# ============================================================
# Solo columnas macro que quieres traer
cols_macro = ["Fecha", "PEA", "desempleo", "tasa_desempleo"]

ventas_vertical_df = pd.merge_asof(
    ventas_vertical_df,
    df_empleo[cols_macro],
    on="Fecha",          # columna común
    direction="backward" # usa el último dato <= Fecha de ventas
)


# ============================================================
# Hacer el merge por Fecha con df_tasa_trimestral
# ============================================================
ventas_vertical_df = ventas_vertical_df.merge(
    df_inpc,
    on="Fecha",
    how="left"
)



# ============================================================
# Hacer el merge por Fecha con pasajeros de OMA
# ============================================================
ventas_vertical_df = ventas_vertical_df.merge(
    oma,
    on="Fecha",
    how="left"
)


# Revisar resultado

 
ventas_vertical_df.head(20)
# ventas_vertical_df.to_csv("ventas_vertical_macro.csv", index=False)

In [ ]:
import pandas as pd

df = ventas_vertical_df.copy()
df["Fecha"] = pd.to_datetime(df["Fecha"])
df = df.sort_values("Fecha")

# Variables a usar
features = [
    "Inventario_disponible",
    "Proyectos_unicos",
    "Precio_por_M2",
    "Precio_promedio",
    "M2_promedio",
    "Numero_de_viviendas_planeadas",
    "tasa_referencia",
    "desempleo"
]

target = "Absorcion_prom_mensual_total"

df_model = df[["Fecha", target] + features].dropna()


In [ ]:
from sklearn.linear_model import ElasticNetCV
from sklearn.preprocessing import StandardScaler
from sklearn.pipeline import Pipeline

X = df_model[features]
y = df_model[target]

pipe = Pipeline([
    ("scaler", StandardScaler()),
    ("model", ElasticNetCV(
        l1_ratio=[0.1, 0.5, 0.9],
        alphas=None,
        cv=5
    ))
])

pipe.fit(X, y)


In [ ]:
coef = pipe.named_steps["model"].coef_

impacto = (
    pd.DataFrame({
        "Variable": features,
        "Coeficiente": coef
    })
    .assign(Impacto_abs=lambda d: d["Coeficiente"].abs())
    .sort_values("Impacto_abs", ascending=False)
)

impacto


In [ ]:
from pandas.tseries.offsets import MonthEnd

last_date = df["Fecha"].max()

future_dates = pd.date_range(
    start=last_date + MonthEnd(1),
    periods=24,
    freq="M"
)

df_future = pd.DataFrame({"Fecha": future_dates})


In [ ]:
df_future["tasa_referencia"] = df["tasa_referencia"].iloc[-1]
df_future["desempleo"] = df["desempleo"].iloc[-1]


In [ ]:
df_future_stress = df_future.copy()
df_future_stress["tasa_referencia"] += 1.5
df_future_stress["desempleo"] += 1.0


In [ ]:
df_future_opt = df_future.copy()
df_future_opt["tasa_referencia"] -= 0.75
df_future_opt["desempleo"] -= 0.5


In [ ]:
for col in [
    "Inventario_disponible",
    "Proyectos_unicos",
    "Precio_por_M2",
    "Precio_promedio",
    "M2_promedio",
    "Numero_de_viviendas_planeadas"
]:
    df_future[col] = df[col].iloc[-1]
    df_future_stress[col] = df[col].iloc[-1]
    df_future_opt[col] = df[col].iloc[-1]


In [ ]:
df_future["Abs_pred_base"] = pipe.predict(df_future[features])
df_future_stress["Abs_pred_stress"] = pipe.predict(df_future_stress[features])
df_future_opt["Abs_pred_opt"] = pipe.predict(df_future_opt[features])


In [ ]:
resultado = df_future[["Fecha", "Abs_pred_base"]].merge(
    df_future_stress[["Fecha", "Abs_pred_stress"]],
    on="Fecha"
).merge(
    df_future_opt[["Fecha", "Abs_pred_opt"]],
    on="Fecha"
)

resultado


In [ ]:
# Preparar datos agregados por tipo de proyecto
# ============================================================

# AFiltro por tipo de proyecto: Horizontal
ventas_horizontal = ventas_con_precio_M2[ventas_con_precio_M2["Tipo_proyecto"] == "Horizontal"]

# Filtrar por proyectos detenidos 
ventas_horizontal = ventas_horizontal[ventas_horizontal['Ventas_detenidas']==0]

# Se agrupan por fecha
ventas_horizontal_agg = (
    ventas_horizontal
    .groupby("Fecha")
    .agg(
        # contar desarrollos únicos en esa fecha
        Proyectos_unicos=("Nombre_desarrollo", "nunique"),
        
        # sumar variables
        Ventas_acumuladas=("Ventas_acumuladas", "sum"),
        Ventas_periodo=("Ventas_periodo", "sum"),
        Inventario_disponible=("Inventario_disponible", "sum"),
        Numero_de_viviendas_planeadas=("Numero_de_viviendas_planeadas", "sum"),
        Ventas_detenidas=("Ventas_detenidas", "sum"),
        
        # promediar variables de “ritmo” / “intensidad” / “características”
        Absorcion_prom_mensual=("Absorcion_prom_mensual", "mean"),
        Precio_promedio=("Precio_promedio", "mean"),
        M2_promedio=("M2_promedio", "mean"),
        Precio_por_M2=("Precio_por_M2", "mean")
    )
    .reset_index()
)
ventas_horizontal_agg.head(20)



In [ ]:
# Preparar datos agregados por tipo de proyecto
# ============================================================

# AFiltro por tipo de proyecto: lote
ventas_lote = ventas_con_precio_M2[ventas_con_precio_M2["Tipo_proyecto"] == "Lote"]

# Filtrar por proyectos detenidos 
ventas_lote = ventas_lote[ventas_lote['Ventas_detenidas']==0]

# Se agrupan por fecha
ventas_lote_agg = (
    ventas_lote
    .groupby("Fecha")
    .agg(
        # contar desarrollos únicos en esa fecha
        Proyectos_unicos=("Nombre_desarrollo", "nunique"),
        
        # sumar variables
        Ventas_acumuladas=("Ventas_acumuladas", "sum"),
        Ventas_periodo=("Ventas_periodo", "sum"),
        Inventario_disponible=("Inventario_disponible", "sum"),
        Numero_de_viviendas_planeadas=("Numero_de_viviendas_planeadas", "sum"),
        Ventas_detenidas=("Ventas_detenidas", "sum"),
        
        # promediar variables de “ritmo” / “intensidad” / “características”
        Absorcion_prom_mensual=("Absorcion_prom_mensual", "mean"),
        Precio_promedio=("Precio_promedio", "mean"),
        M2_promedio=("M2_promedio", "mean"),
        Precio_por_M2=("Precio_por_M2", "mean")
    )
    .reset_index()
)
ventas_lote_agg.head(20)

# Guardar datos del modelo, rentrenarlo, mejorar del modelo continuo

In [ ]:
# ============================================================
# 9. GUARDAR MODELOS Y PROYECCIONES (MEJORA CONTINUA)
# ============================================================

output_dir = Path("model_output")
output_dir.mkdir(exist_ok=True)

# Guardar modelos
model_path = output_dir / "modelos_ventas.pkl"
joblib.dump(modelos, model_path)

# Guardar información adicional (features, etc.)
info_path = output_dir / "info_modelos.pkl"
joblib.dump(info_modelos, info_path)

# Guardar predicciones a Excel/CSV
predicciones_path = output_dir / "predicciones_24_meses.xlsx"
predicciones_24meses.to_excel(predicciones_path, index=False)

print(f"Modelos guardados en: {model_path}")
print(f"Info modelos guardada en: {info_path}")
print(f"Predicciones guardadas en: {predicciones_path}")


In [ ]:
# ============================================================
# 10. FUNCIÓN PARA CARGAR MODELOS Y RE-ENTRENAR CON NUEVOS DATOS
# ============================================================

def cargar_modelos_y_info(output_dir=Path("model_output")):
    modelos = joblib.load(output_dir / "modelos_ventas.pkl")
    info    = joblib.load(output_dir / "info_modelos.pkl")
    return modelos, info

def reentrenar_con_nuevos_datos(nuevas_ventas_df, modelos, info_modelos, features_por_tipo):
    """
    Lógica general para re-entrenar:
    - Combinar nuevas ventas con las históricas.
    - Reconstruir dataset por tipo.
    - Re-entrenar modelos.
    
    NOTA: Aquí se asume que nuevas_ventas_df tiene la misma estructura que ventas_df original.
    """
    # 1) Concatenar histórico + nuevos datos
    ventas_total = pd.concat([ventas_df, nuevas_ventas_df], ignore_index=True)
    
    # 2) Volver a preparar datasets por tipo
    dataset_vertical   = preparar_dataset_por_tipo(ventas_total, features_por_tipo, "Vertical")
    dataset_horizontal = preparar_dataset_por_tipo(ventas_total, features_por_tipo, "Horizontal")
    dataset_lote       = preparar_dataset_por_tipo(ventas_total, features_por_tipo, "Lote")
    
    # 3) Volver a entrenar
    nuevos_modelos = {}
    nueva_info_modelos = {}
    
    for tipo, dataset in zip(
        ["Vertical", "Horizontal", "Lote"],
        [dataset_vertical, dataset_horizontal, dataset_lote]
    ):
        clf, X_train, X_test, y_train, y_test, feature_cols = entrenar_modelo_tipo(dataset, tipo)
        nuevos_modelos[tipo] = clf
        nueva_info_modelos[tipo] = {
            "X_train": X_train,
            "X_test":  X_test,
            "y_train": y_train,
            "y_test":  y_test,
            "feature_cols": feature_cols,
            "dataset": dataset
        }
    
    return nuevos_modelos, nueva_info_modelos
